In [75]:
import pandas as pd
import numpy as np
import time
import sklearn.preprocessing as sk
from sklearn import svm
from keras.models import Sequential
from keras.layers import *
from keras.optimizers import *
from sklearn.decomposition import PCA

In [2]:
# A method to fix the API
def fixAPI(API):
    if API[0]=='5':
        API = '0'+API
    return API

In [3]:
# Reading the data
start = time.time()
production_data_train = pd.read_csv("production_data_train.csv",dtype={'API':str})
end = time.time()
print('ReadData',end-start)

ReadData 0.5090291500091553


In [4]:
# Fix api
start = time.time()
production_data_train["API"] = production_data_train["API"].apply(fixAPI)
end = time.time()
print('FixApi',end-start)

FixApi 0.06400346755981445


In [5]:
# Removing duplicates
start = time.time()
production_data_train = production_data_train.sort_values(['_LastUpdate'])
production_data_train.drop_duplicates(subset=['API','Year','Month'],keep='last',inplace=True)
end = time.time()
print('RemovingDuplicates',end-start)

RemovingDuplicates 0.5380308628082275


In [6]:
# Remove pre-peek month
start = time.time()
maxLiquid = production_data_train.groupby(['API'],as_index=False).agg({'Liquid':'max'})
maxDate = pd.merge(maxLiquid[['API','Liquid']],production_data_train[['API','Liquid','Year','Month']],on=['API','Liquid'],how='left')

max1 = maxDate.groupby(['API','Liquid'],as_index=False).agg({'Year':'min'})
maxDate = pd.merge(maxDate[['API','Liquid','Year','Month']],max1[['API','Liquid','Year']],on=['API','Liquid','Year'],how='right')
maxDate = maxDate.groupby(['API','Liquid','Year'],as_index=False).agg({'Month':'min'})

maxDate = maxDate[['API','Year','Month']]
maxDate = maxDate.rename(columns={"Year":"maxYear",'Month':'maxMonth'})
production_data_train = pd.merge(production_data_train,maxDate[['API','maxYear','maxMonth']],on='API')
production_data_train = production_data_train[((production_data_train['Year']-production_data_train['maxYear'])*12+production_data_train['Month']-production_data_train['maxMonth'])>=0]

end = time.time()
print('RemovePrePeekMonth',end-start)

RemovePrePeekMonth 0.42902445793151855


In [7]:
# Adding Index
start = time.time()
production_data_train["Index"] = (production_data_train["Year"]-production_data_train['maxYear'])*12+production_data_train["Month"]-production_data_train["maxMonth"]+1
end = time.time()
print('IndexColumn',end-start)

IndexColumn 0.059003353118896484


In [8]:
production_data_train

API  Year  Month  Liquid    Gas  RatioGasOil  Water  \
0       33053063590000  2015      6   10421  12311     1.181365   2717   
1       33053063590000  2015      7    9777  11254     1.151069   2399   
2       33053063590000  2015      8   10613  12188     1.148403   2742   
3       33053063590000  2015      9   13119  17739     1.352161   2903   
4       33053063590000  2015     10   10318  12979     1.257899   2286   
5       33053063590000  2015     11    8126   9642     1.186562   1795   
6       33053063590000  2016      3    6793   8367     1.231709   1803   
7       33053063590000  2016      4    7325  11139     1.520683   1798   
8       33053063590000  2016      5    7381  15601     2.113670   1975   
9       33053063590000  2015     12    7527   7570     1.005713   1679   
10      33053063590000  2015      5   14626  15988     1.093122   4213   
11      33053063590000  2015      4   18796  21796     1.159608   7255   
12      33053063590000  2016      1    7934   8823     1.112049   1943   
13      33053063590000  2016      6    5975  11362     1.901590   1610   
15      33053063590000  2016      8    5390   8475     1.572356   1417   
16      33053063590000  2016      9    4626   6954     1.503243   1223   
17      33053063590000  2016     10    3432   4814     1.402681    899   
18      33053063590000  2017      3    1624   1590     0.979064    366   
19      33053063590000  2017      4     829    941     1.135103    195   
20      33053063590000  2017      5    1912   1964     1.027197   2619   
21      33053063590000  2017      6    6338   7363     1.161723   2617   
22      33053063590000  2017      7    6182   7996     1.293433   2005   
23      33053063590000  2017      9    4864   6915     1.421669   1484   
24      33053063590000  2017     10    4617   6937     1.502491   1335   
25      33053063590000  2017     11    4185   6196     1.480526   1342   
26      33053063590000  2017      8    5345   7149     1.337512   1643   
27      33053063590000  2017     12    3770   5121     1.358355   1147   
28      33053063590000  2018      1    3194   3696     1.157170    977   
29      33053063590000  2016      2    7337  10581     1.442143   1783   
30      33053063590000  2016     12    3688   3998     1.084056   2066   
...                ...   ...    ...     ...    ...          ...    ...   
394033  42301324920100  2016     10    3155   6221     1.971791  22023   
394034  42301324920100  2016     11    2687   6382     2.375140  18719   
394035  42301324920100  2016      1    4073   4162     1.021851  22479   
394036  42301324920100  2017      1    2162   4021     1.859852  15072   
394037  42301324920100  2017      8    2487   4485     1.803378  19958   
394038  42301324920100  2017      3    3542   5806     1.639187  26627   
394039  42301324920100  2018      7    7432   9536     1.283100  66864   
394040  42301324920100  2018      6    4531   8700     1.920106  40840   
394041  42301324920100  2018      5    2387  10603     4.441977  21452   
394042  42301324920100  2018      4    3571   3083     0.863344  32145   
394043  42301324920100  2018      3    1759   2928     1.664582  15769   
394044  42301324920100  2018      2    4791   6731     1.404926  43147   
394045  42301324920100  2018      1    1974   3006     1.522796  16686   
394046  42301324920100  2017      2    1796   3636     2.024499  13498   
394047  42301324920100  2017     12    2772   4049     1.460678  23671   
394048  42301324920100  2017     10    1469   5380     3.662355  12596   
394049  42301324920100  2017      9    1007   2896     2.875869   7967   
394050  42301324920100  2015      9    8387  13538     1.614165  41875   
394051  42301324920100  2017      7    1421   2205     1.551724  11337   
394052  42301324920100  2017      6    2633   1986     0.754273  21004   
394053  42301324920100  2017      5    2645   4511     1.705482  19915   
394054  42301324920100  2017      4    1615   4372     2.707121  12083   
394055  42301324920100 

In [9]:
# Getting the training labels (3_yrs_cum_oil production)
temp = production_data_train[production_data_train["Index"]<=36]
y_train = temp.groupby("API").agg({'Liquid':'sum'})
y_train

Liquid
API                   
05001097720000   65412
05001097780100   84043
05001097800000   13471
05001097820000   12992
05001097830000   15195
05001098050100  176206
05001098450000  180189
05005071800000  126323
05005071890100   66150
05005071920000  186252
05005072090000  142882
05005072120000   62652
05005072140100   63836
05005072150100   99022
05005072170100  234552
05005072190100  264294
05005072210000  250013
05005072220000  102986
05005072250100  200616
05005072260000  217756
05123315730000   20563
05123331840000   17377
05123334240100   20788
05123349460000   91506
05123349600000   76262
05123349910100    7703
05123350610000   70095
05123350770000   91265
05123352460000   28831
05123352590000   51454
...                ...
49021211170000  180118
49021211180000  133436
49021211280000  142229
49021211310000  201533
49021211320000   87110
49021211460000   73927
49021211760000   31937
49021211780000  207008
49021211800000  236270
49021211820000  191163
49021212030000  146182
49021212280000  164647
49021212460000  222063
49021212470000  187938
49021212490000  236922
49021213620000   95972
49021213990000   90304
49021214000000   31496
49021214010000   41765
49021215910000   88956
49021217890000   63698
49021219480000  134031
49021221450000  161373
49021222690000  106619
49021222710000   71089
49021222940000  227454
49021222950000  211789
49021223030000  230485
49021226570000   26615
49021226580100   31585

[7844 rows x 1 columns]

In [10]:
# reading the features CSVs
Harmony_data = pd.read_csv("Harmony_data.csv",dtype={'API':str})
IHS_data = pd.read_csv("IHS_data.csv",dtype={'API':str,'FirstProductionDate':str})
# fixing the APIs
Harmony_data["API"] = Harmony_data["API"].apply(fixAPI)
IHS_data["API"] = IHS_data["API"].apply(fixAPI)

In [11]:
# making an initial set of training features with the Harmony data only
temp2 = pd.merge(y_train,Harmony_data,on='API',how = 'left')
temp2.fillna(0,inplace = True)
temp2

API  Liquid  LATERAL_LENGTH_BLEND  PROP_PER_FOOT  \
0     05001097720000   65412                  4358       760.4881   
1     05001097780100   84043                  4208       611.6503   
2     05001097800000   13471                  3983         0.0000   
3     05001097820000   12992                  4221       801.2611   
4     05001097830000   15195                  4027         0.0000   
5     05001098050100  176206                  8190      1408.8110   
6     05001098450000  180189                  4315         0.0000   
7     05005071800000  126323                  4053      3401.1990   
8     05005071890100   66150                  3745      1742.2890   
9     05005071920000  186252                  3866      1835.5640   
10    05005072090000  142882                  4079      1568.7120   
11    05005072120000   62652                  3262      1914.9830   
12    05005072140100   63836                  3841      1738.0710   
13    05005072150100   99022                  3787         0.0000   
14    05005072170100  234552                  9005       994.6866   
15    05005072190100  264294                  6720      1876.9140   
16    05005072210000  250013                  8545      1252.0050   
17    05005072220000  102986                  3815      1876.9190   
18    05005072250100  200616                  6440       875.3403   
19    05005072260000  217756                  8540      1369.7750   
20    05123315730000   20563                  3554      1365.6510   
21    05123331840000   17377                  4012         0.0000   
22    05123334240100   20788                  3508       834.5635   
23    05123349460000   91506                  4589       221.6403   
24    05123349600000   76262                  4173       782.5092   
25    05123349910100    7703                  2550         0.0000   
26    05123350610000   70095                  4105      1178.6280   
27    05123350770000   91265                  4038       651.1269   
28    05123352460000   28831                  8813       875.0183   
29    05123352590000   51454                  3902         0.0000   
...              ...     ...                   ...            ...   
7814  49021211170000  180118                  9434       646.8029   
7815  49021211180000  133436                  9678       639.8415   
7816  49021211280000  142229                  8897      1316.9290   
7817  49021211310000  201533                  9341      1312.9230   
7818  49021211320000   87110                  9642       613.0061   
7819  49021211460000   73927                  6647      1172.1610   
7820  49021211760000   31937                  4059      1198.5090   
7821  49021211780000  207008                  9014      1350.5770   
7822  49021211800000  236270                  9445      1296.2060   
7823  49021211820000  191163                  8930      1398.2330   
7824  49021212030000  146182                  9457      1307.2390   
7825  49021212280000  164647                  9480      1077.4830   
7826  49021212460000  222063                  8971      2424.1120   
7827  49021212470000  187938                  8627      2391.5970   
7828  49021212490000  236922                  9382      2143.3760   
7829  49021213620000   95972                  9710       562.3441   
7830  49021213990000   90304                  9684       584.5623   
7831  49021214000000   31496                  4714       552.4348   
7832  49021214010000   41765                  4779       266.3333   
7833  49021215910000   88956                  9784       543.0637   
7834  49021217890000   63698                  1659       522.7615   
7835  49021219480000  134031                  9705      1297.6180   
7836  49021221450000  161373                  9670       437.8219   
7837  49021222690000  106619                  9822       572.4443   
7838  49021222710000   71089                  9527       622.4385   
7839  49021222940000  227454                 10138      2534.0880   
7840  490212229

In [12]:
x_train = temp2.drop(['API','Liquid'], axis=1)
x_train

LATERAL_LENGTH_BLEND  PROP_PER_FOOT  WATER_PER_FOOT       GOR_30  \
0                     4358       760.4881        934.0413  2841.940260   
1                     4208       611.6503        546.6923  2420.241440   
2                     3983         0.0000          0.0000  2076.526858   
3                     4221       801.2611        505.2079  3652.173913   
4                     4027         0.0000          0.0000  2457.326098   
5                     8190      1408.8110          0.0000  1598.716588   
6                     4315         0.0000          0.0000  1407.787232   
7                     4053      3401.1990       2065.5310  1216.537860   
8                     3745      1742.2890       1807.3310  2059.910523   
9                     3866      1835.5640       1890.1990  3186.014597   
10                    4079      1568.7120       1630.7050  1654.373024   
11                    3262      1914.9830       1672.1780  2018.015596   
12                    3841      1738.0710       1281.4290  1905.849582   
13                    3787         0.0000          0.0000  1322.132647   
14                    9005       994.6866        591.8004  1249.318351   
15                    6720      1876.9140       1618.9850  1214.378209   
16                    8545      1252.0050       1235.5770  1061.961113   
17                    3815      1876.9190       1047.6740  1308.664642   
18                    6440       875.3403       1035.7760  2729.685603   
19                    8540      1369.7750       1313.5470  2009.318579   
20                    3554      1365.6510       1012.7990   498.804543   
21                    4012         0.0000          0.0000  3247.303236   
22                    3508       834.5635        651.6735  3074.136764   
23                    4589       221.6403        131.7694  2099.389996   
24                    4173       782.5092        594.7244  3173.713704   
25                    2550         0.0000        801.4464   605.031447   
26                    4105      1178.6280        807.1788  1976.423416   
27                    4038       651.1269        526.2178  2034.171413   
28                    8813       875.0183        464.8092  3757.302405   
29                    3902         0.0000          0.0000  3007.571259   
...                    ...            ...             ...          ...   
7814                  9434       646.8029          0.0000   330.741734   
7815                  9678       639.8415          0.0000   418.323704   
7816                  8897      1316.9290        662.2171   607.470289   
7817                  9341      1312.9230        849.5093   694.357309   
7818                  9642       613.0061          0.0000   569.349788   
7819                  6647      1172.1610        674.7793  1139.989029   
7820                  4059      1198.5090          0.0000   692.955112   
7821                  9014      1350.5770        838.8643   809.819371   
7822                  9445      1296.2060        812.3987  1169.257483   
7823                  8930      1398.2330        879.5729   495.476819   
7824                  9457      1307.2390        835.6952   843.114626   
7825                  9480      1077.4830        847.9736   611.024075   
7826                  8971      2424.1120       1348.6120   609.965988   
7827                  8627      2391.5970       1441.0970   454.680978   
7828                  9382      2143.3760       1241.4700   609.038127   
7829                  9710       562.3441          0.0000   534.401136   
7830                  9684       584.5623          0.0000   556.290893   
7831                  4714       552.4348          0.0000   543.292103   
7832                  4779       266.3333          0.0000   397.645115   
7833                  9784       543.0637          0.0000   587.270156   
7834                  1659       522.7615          0.0000   495.260664   
7835                  9705      1297.6180        876.0724   674.773118   
7836      

In [13]:
x_train = np.array(x_train)
y_train = np.array(y_train) 
y_train.shape
x_train.shape
print(x_train.shape,y_train.shape)

(7844, 6) (7844, 1)


In [14]:
# normalize training data
# x_train = sk.normalize(x_train)
x_train

array([[4358.        ,  760.4881    ,  934.0413    , 2841.94025951,
        3126.39585693, 3270.49944883],
       [4208.        ,  611.6503    ,  546.6923    , 2420.24143953,
        2878.66692315, 2799.40106766],
       [3983.        ,    0.        ,    0.        , 2076.52685798,
        1289.76123027,  936.7157665 ],
       ...,
       [8161.        , 2202.056     , 1387.139     ,  542.96133666,
         472.57393067,  517.34242223],
       [4208.        ,  584.2202    ,  217.9879    ,  416.33986928,
         405.864774  ,  366.30466686],
       [4249.        ,  538.438     ,    0.        ,  355.67514677,
         410.45096636,  464.87159181]])

In [15]:
# creating the Machine Learning model
model = Sequential()
model.add(Dense(output_dim=4, activation=LeakyReLU(alpha=0.3), input_dim=x_train.shape[1]))
# model.add(Dense(output_dim=4, activation=LeakyReLU(alpha=0.3)))
model.add(Dense(output_dim=y_train.shape[1], activation='linear'))
adam = Adam(lr=0.1)
model.compile(loss='mae', optimizer=adam)

Instructions for updating:
Colocations handled automatically by placer.


c:\users\gigabyte\appdata\local\programs\python\python37\lib\site-packages\ipykernel_launcher.py:3: UserWarning: Update your `Dense` call to the Keras 2 API: `Dense(activation=<keras.lay..., input_dim=6, units=4)`
  This is separate from the ipykernel package so we can avoid doing imports until
c:\users\gigabyte\appdata\local\programs\python\python37\lib\site-packages\keras\activations.py:211: UserWarning: Do not pass a layer instance (such as LeakyReLU) as the activation argument of another layer. Instead, advanced activation layers should be used just like any other layer in a model.
  identifier=identifier.__class__.__name__))
c:\users\gigabyte\appdata\local\programs\python\python37\lib\site-packages\ipykernel_launcher.py:5: UserWarning: Update your `Dense` call to the Keras 2 API: `Dense(activation="linear", units=1)`
  """


In [41]:
# fitting the model
model.fit(x_train,y_train,batch_size = 512, epochs= 20000 , verbose = 1,shuffle = True)

Epoch 1/20000
7844/7844 [==============================] - 0s 32us/step - loss: 104778.0182
Epoch 2/20000
7844/7844 [==============================] - 0s 2us/step - loss: 59465.9054
Epoch 3/20000
7844/7844 [==============================] - 0s 2us/step - loss: 52908.9886
Epoch 4/20000
7844/7844 [==============================] - 0s 2us/step - loss: 51379.8496
Epoch 5/20000
7844/7844 [==============================] - 0s 2us/step - loss: 50998.1037
Epoch 6/20000
7844/7844 [==============================] - 0s 2us/step - loss: 50686.4030
Epoch 7/20000
7844/7844 [==============================] - 0s 2us/step - loss: 50705.7062
Epoch 8/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50650.3823
Epoch 9/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50820.9538
Epoch 10/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50860.9768
Epoch 11/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50678.7742
Epoch 

7844/7844 [==============================] - 0s 1us/step - loss: 50814.4549
Epoch 92/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50834.4421
Epoch 93/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50544.9886
Epoch 94/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50854.3140
Epoch 95/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50757.8117
Epoch 96/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50596.1213
Epoch 97/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50581.3684
Epoch 98/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50581.5017
Epoch 99/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50583.8534
Epoch 100/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50532.2215
Epoch 101/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50545.3023
Epoch 102/20

7844/7844 [==============================] - 0s 1us/step - loss: 50234.1262
Epoch 270/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50213.6568
Epoch 271/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50102.9611
Epoch 272/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50331.4518
Epoch 273/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50281.6324
Epoch 274/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50320.8415
Epoch 275/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50542.2528
Epoch 276/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50209.3340
Epoch 277/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50422.7294
Epoch 278/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50194.1744
Epoch 279/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50260.3208
Epoc

7844/7844 [==============================] - 0s 1us/step - loss: 50315.0993
Epoch 448/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50039.6881
Epoch 449/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50022.1408
Epoch 450/20000
7844/7844 [==============================] - 0s 2us/step - loss: 50039.6046
Epoch 451/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49912.8458
Epoch 452/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50244.3081
Epoch 453/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50071.7110
Epoch 454/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50152.9064
Epoch 455/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50068.2909
Epoch 456/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50127.8479
Epoch 457/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50035.2381
Epoc

7844/7844 [==============================] - 0s 1us/step - loss: 49972.7372
Epoch 626/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49977.7132
Epoch 627/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50016.4571
Epoch 628/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49951.8160
Epoch 629/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49996.0275
Epoch 630/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50079.1089
Epoch 631/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50081.8883
Epoch 632/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50009.3890
Epoch 633/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50137.6500
Epoch 634/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50101.1763
Epoch 635/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50185.1556
Epoc

...

7844/7844 [==============================] - 0s 1us/step - loss: 49529.8610
Epoch 19179/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49667.0002
Epoch 19180/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49601.5267
Epoch 19181/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49350.8618
Epoch 19182/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49572.8149
Epoch 19183/20000
7844/7844 [==============================] - 0s 2us/step - loss: 49539.3698
Epoch 19184/20000
7844/7844 [==============================] - 0s 2us/step - loss: 49325.8122
Epoch 19185/20000
7844/7844 [==============================] - 0s 2us/step - loss: 49270.6363
Epoch 19186/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49137.3056
Epoch 19187/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49318.8720
Epoch 19188/20000
7844/7844 [==============================] - 0s 1us/step - l

7844/7844 [==============================] - 0s 1us/step - loss: 49796.8992
Epoch 19353/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50750.4759
Epoch 19354/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49267.7026
Epoch 19355/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49203.1828
Epoch 19356/20000
7844/7844 [==============================] - 0s 2us/step - loss: 49503.7411
Epoch 19357/20000
7844/7844 [==============================] - 0s 2us/step - loss: 49437.3648
Epoch 19358/20000
7844/7844 [==============================] - 0s 2us/step - loss: 49479.8822
Epoch 19359/20000
7844/7844 [==============================] - 0s 2us/step - loss: 49572.6591
Epoch 19360/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49989.2844
Epoch 19361/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49483.7550
Epoch 19362/20000
7844/7844 [==============================] - 0s 1us/step - l

7844/7844 [==============================] - 0s 1us/step - loss: 49232.2771
Epoch 19527/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49188.3588
Epoch 19528/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49146.9407
Epoch 19529/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49377.8899
Epoch 19530/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49499.5782
Epoch 19531/20000
7844/7844 [==============================] - 0s 2us/step - loss: 49654.8453
Epoch 19532/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50039.0862
Epoch 19533/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49275.1250
Epoch 19534/20000
7844/7844 [==============================] - 0s 2us/step - loss: 49588.6130
Epoch 19535/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49331.4349
Epoch 19536/20000
7844/7844 [==============================] - 0s 1us/step - l

7844/7844 [==============================] - 0s 1us/step - loss: 49630.3209
Epoch 19701/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49422.9777
Epoch 19702/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49229.3096
Epoch 19703/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49221.9530
Epoch 19704/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49395.1608
Epoch 19705/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49605.5098
Epoch 19706/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49294.5250
Epoch 19707/20000
7844/7844 [==============================] - 0s 2us/step - loss: 49552.8770
Epoch 19708/20000
7844/7844 [==============================] - 0s 2us/step - loss: 49662.3290
Epoch 19709/20000
7844/7844 [==============================] - 0s 2us/step - loss: 49180.1152
Epoch 19710/20000
7844/7844 [==============================] - 0s 1us/step - l

7844/7844 [==============================] - 0s 1us/step - loss: 49481.6888
Epoch 19875/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49228.2323
Epoch 19876/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49380.3393
Epoch 19877/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49259.7178
Epoch 19878/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49112.5142
Epoch 19879/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49916.4246
Epoch 19880/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49493.4713
Epoch 19881/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49200.2096
Epoch 19882/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49203.5039
Epoch 19883/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49314.5372
Epoch 19884/20000
7844/7844 [==============================] - 0s 1us/step - l

In [15]:
# Dropping the dates from the IHS data file
temp3 = IHS_data.drop(['PermitDate','SpudDate','CompletionDate'], axis=1)
temp3

API      FirstProductionDate  \
0      33061020640000  2013-01-01 00:00:00.000   
1      25083228390000  2010-10-01 00:00:00.000   
2      25083231000000  2013-11-01 00:00:00.000   
3      33053032050000  2011-07-01 00:00:00.000   
4      25083228880100  2011-11-01 00:00:00.000   
5      33053031440000  2010-06-01 00:00:00.000   
6      33025023360000  2017-04-01 00:00:00.000   
7      33023006690000  2011-02-01 00:00:00.000   
8      33013015390000  2012-03-01 00:00:00.000   
9      33025012270000  2011-11-01 00:00:00.000   
10     33023006700000  2011-08-01 00:00:00.000   
11     25085218680000  2013-03-01 00:00:00.000   
12     33061016590000  2011-09-01 00:00:00.000   
13     33105020500100  2011-07-01 00:00:00.000   
14     33105018960000  2010-10-01 00:00:00.000   
15     33053063280000  2017-12-01 00:00:00.000   
16     33053032540000  2010-12-01 00:00:00.000   
17     33055001750000  2016-10-01 00:00:00.000   
18     33105020810000  2012-01-01 00:00:00.000   
19     25083228990000  2012-01-01 00:00:00.000   
20     25083231090000  2013-08-01 00:00:00.000   
21     25083231910000  2014-05-01 00:00:00.000   
22     33061011010000  2010-04-01 00:00:00.000   
23     33023006610000  2011-04-01 00:00:00.000   
24     33025012640000  2011-06-01 00:00:00.000   
25     33061014200000  2010-11-01 00:00:00.000   
26     33007016630000  2011-02-01 00:00:00.000   
27     25083228310000  2010-08-01 00:00:00.000   
28     33061013910000  2011-08-01 00:00:00.000   
29     33053061700000  2018-05-01 00:00:00.000   
...               ...                      ...   
48935  33053080160100  2018-07-01 00:00:00.000   
48936  42389370910000  2018-08-01 00:00:00.000   
48937  42475373790200  2018-02-01 00:00:00.000   
48938  42227396070000  2018-08-01 00:00:00.000   
48939  42329424940000  2018-10-01 00:00:00.000   
48940  42461408670000  2018-10-01 00:00:00.000   
48941  42461408690000  2018-10-01 00:00:00.000   
48942  42475372330100  2018-08-01 00:00:00.000   
48943  42227396260000  2018-08-01 00:00:00.000   
48944  42301340140000                      NaN   
48945  42389371540000  2018-09-01 00:00:00.000   
48946  42329422560200  2018-07-01 00:00:00.000   
48947  42301331460100  2018-07-01 00:00:00.000   
48948  30015449720000  2018-10-01 00:00:00.000   
48949  42371397530000  2018-09-01 00:00:00.000   
48950  42389371720000  2018-10-01 00:00:00.000   
48951  42371395510100  2018-05-01 00:00:00.000   
48952  33025033360100  2018-05-01 00:00:00.000   
48953  35049252030000  2018-10-01 00:00:00.000   
48954  42227396450000  2018-09-01 00:00:00.000   
48955  30025449040000  2018-09-01 00:00:00.000   
48956  35017252380000                      NaN   
48957  42383403290000                      NaN   
48958  42329422110100                      NaN   
48959  42461406570100  2018-05-01 00:00:00.000   
48960  42475374150300  2018-06-01 00:00:00.000   
48961  42475375400100  2018-08-01 00:00:00.000   
48962  30015446810100  2018-08-01 00:00:00.000   
48963  42301338440100  2018-09-01 00:00:00.000   
48964  33105046000100  2018-05-01 00:00:00.000   

                           operatorNameIHS                 formation  \
0       CONTINENTAL RESOURCES INCORPORATED                    BAKKEN   
1                  XTO ENERGY INCORPORATED                    BAKKEN   
2                     KRAKEN OPERATING LLC                    BAKKEN   
3           BURLINGTON RESOURCES O&G CO LP                    BAKKEN   
4       CONTINENTAL RESOURCES INCORPORATED                    BAKKEN   
5       CONTINENTAL RESOURCES INCORPORATED                    BAKKEN   
6                 WPX ENERGY WILLISTON LLC                    BAKKEN   
7       CONTINENTAL RESOURCES INCORPORATED                    BAKKEN   
8               EOG RESOURCES INCORPORATED                    BAKKEN   
9                         HUNT OIL COMPANY                    BAKKEN   
10      CONTINENTAL RESOURCES INCORPORATED                    BAKKEN   
11              EOG RESOURCES INCORPORATED           

In [16]:
def getYear(x):
    x = str(x)
    y = x[0:4]
    return y

In [17]:
temp3["FirstProductionDate"] = temp3["FirstProductionDate"].apply(getYear)
temp3["FirstProductionDate"] = pd.to_numeric(temp3["FirstProductionDate"],errors='coerce')
temp3["FirstProductionDate"].mean()
temp3["FirstProductionDate"].fillna(temp3["FirstProductionDate"].mean(),inplace = True)
temp3["FirstProductionDate"] = pd.Series(temp3["FirstProductionDate"], dtype='int32')
temp3["FirstProductionDate"]

0        2013
1        2010
2        2013
3        2011
4        2011
5        2010
6        2017
7        2011
8        2012
9        2011
10       2011
11       2013
12       2011
13       2011
14       2010
15       2017
16       2010
17       2016
18       2012
19       2012
20       2013
21       2014
22       2010
23       2011
24       2011
25       2010
26       2011
27       2010
28       2011
29       2018
         ... 
48935    2018
48936    2018
48937    2018
48938    2018
48939    2018
48940    2018
48941    2018
48942    2018
48943    2018
48944    2014
48945    2018
48946    2018
48947    2018
48948    2018
48949    2018
48950    2018
48951    2018
48952    2018
48953    2018
48954    2018
48955    2018
48956    2014
48957    2014
48958    2014
48959    2018
48960    2018
48961    2018
48962    2018
48963    2018
48964    2018
Name: FirstProductionDate, Length: 48965, dtype: int32

In [18]:
# temp3["FirstProductionDate"].fillna()

In [19]:
d = {}
i = 0
for name in temp3.operatorNameIHS.unique():
    d[name] = i
    i += 1
temp3.replace({'operatorNameIHS': d},inplace = True)

d = {}
i = 0
for name in temp3.formation.unique():
    d[name] = i
    i += 1
temp3.replace({'formation': d},inplace = True)

d = {}
i = 0
for name in temp3.BasinName.unique():
    d[name] = i
    i += 1
temp3.replace({'BasinName': d},inplace = True)

d = {}
i = 0
for name in temp3.StateName.unique():
    d[name] = i
    i += 1
temp3.replace({'StateName': d},inplace = True)

d = {}
i = 0
for name in temp3.CountyName.unique():
    d[name] = i
    i += 1
temp3.replace({'CountyName': d},inplace = True)
temp3

API  FirstProductionDate  operatorNameIHS  formation  \
0      33061020640000                 2013                0          0   
1      25083228390000                 2010                1          0   
2      25083231000000                 2013                2          0   
3      33053032050000                 2011                3          0   
4      25083228880100                 2011                0          0   
5      33053031440000                 2010                0          0   
6      33025023360000                 2017                4          0   
7      33023006690000                 2011                0          0   
8      33013015390000                 2012                5          0   
9      33025012270000                 2011                6          0   
10     33023006700000                 2011                0          0   
11     25085218680000                 2013                5          0   
12     33061016590000                 2011                5          0   
13     33105020500100                 2011                0          0   
14     33105018960000                 2010                5          0   
15     33053063280000                 2017                7          0   
16     33053032540000                 2010                0          0   
17     33055001750000                 2016                4          0   
18     33105020810000                 2012                5          0   
19     25083228990000                 2012                0          0   
20     25083231090000                 2013                0          0   
21     25083231910000                 2014                0          0   
22     33061011010000                 2010                5          0   
23     33023006610000                 2011                0          0   
24     33025012640000                 2011                0          0   
25     33061014200000                 2010                6          0   
26     33007016630000                 2011                0          0   
27     25083228310000                 2010                5          0   
28     33061013910000                 2011                8          0   
29     33053061700000                 2018                9          0   
...               ...                  ...              ...        ...   
48935  33053080160100                 2018               12         27   
48936  42389370910000                 2018               97        216   
48937  42475373790200                 2018               71        216   
48938  42227396070000                 2018              354        171   
48939  42329424940000                 2018              544        171   
48940  42461408670000                 2018              352        171   
48941  42461408690000                 2018              352        171   
48942  42475372330100                 2018               53        216   
48943  42227396260000                 2018              354        171   
48944  42301340140000                 2014              560        216   
48945  42389371540000                 2018              154        220   
48946  42329422560200                 2018              352        171   
48947  42301331460100                 2018                5        216   
48948  30015449720000                 2018               64        216   
48949  42371397530000                 2018               83        216   
48950  42389371720000                 2018               77        220   
48951  42371395510100                 2018              568        220   
48952  33025033360100                 2018                4         27   
48953  35049252030000                 2018              473        239   
48954  42227396450000                 2018              354        171   
48955  30025449040000                 2018                5        217   
48956  35017252380000                 2014              439        207   
48957  42383403290000 

In [20]:
temp4 = pd.merge(temp2,temp3,on='API',how = 'left')
temp4

API  Liquid  LATERAL_LENGTH_BLEND  PROP_PER_FOOT  \
0     05001097720000   65412                  4358       760.4881   
1     05001097780100   84043                  4208       611.6503   
2     05001097800000   13471                  3983         0.0000   
3     05001097820000   12992                  4221       801.2611   
4     05001097830000   15195                  4027         0.0000   
5     05001098050100  176206                  8190      1408.8110   
6     05001098450000  180189                  4315         0.0000   
7     05005071800000  126323                  4053      3401.1990   
8     05005071890100   66150                  3745      1742.2890   
9     05005071920000  186252                  3866      1835.5640   
10    05005072090000  142882                  4079      1568.7120   
11    05005072120000   62652                  3262      1914.9830   
12    05005072140100   63836                  3841      1738.0710   
13    05005072150100   99022                  3787         0.0000   
14    05005072170100  234552                  9005       994.6866   
15    05005072190100  264294                  6720      1876.9140   
16    05005072210000  250013                  8545      1252.0050   
17    05005072220000  102986                  3815      1876.9190   
18    05005072250100  200616                  6440       875.3403   
19    05005072260000  217756                  8540      1369.7750   
20    05123315730000   20563                  3554      1365.6510   
21    05123331840000   17377                  4012         0.0000   
22    05123334240100   20788                  3508       834.5635   
23    05123349460000   91506                  4589       221.6403   
24    05123349600000   76262                  4173       782.5092   
25    05123349910100    7703                  2550         0.0000   
26    05123350610000   70095                  4105      1178.6280   
27    05123350770000   91265                  4038       651.1269   
28    05123352460000   28831                  8813       875.0183   
29    05123352590000   51454                  3902         0.0000   
...              ...     ...                   ...            ...   
7814  49021211170000  180118                  9434       646.8029   
7815  49021211180000  133436                  9678       639.8415   
7816  49021211280000  142229                  8897      1316.9290   
7817  49021211310000  201533                  9341      1312.9230   
7818  49021211320000   87110                  9642       613.0061   
7819  49021211460000   73927                  6647      1172.1610   
7820  49021211760000   31937                  4059      1198.5090   
7821  49021211780000  207008                  9014      1350.5770   
7822  49021211800000  236270                  9445      1296.2060   
7823  49021211820000  191163                  8930      1398.2330   
7824  49021212030000  146182                  9457      1307.2390   
7825  49021212280000  164647                  9480      1077.4830   
7826  49021212460000  222063                  8971      2424.1120   
7827  49021212470000  187938                  8627      2391.5970   
7828  49021212490000  236922                  9382      2143.3760   
7829  49021213620000   95972                  9710       562.3441   
7830  49021213990000   90304                  9684       584.5623   
7831  49021214000000   31496                  4714       552.4348   
7832  49021214010000   41765                  4779       266.3333   
7833  49021215910000   88956                  9784       543.0637   
7834  49021217890000   63698                  1659       522.7615   
7835  49021219480000  134031                  9705      1297.6180   
7836  49021221450000  161373                  9670       437.8219   
7837  49021222690000  106619                  9822       572.4443   
7838  49021222710000   71089                  9527       622.4385   
7839  49021222940000  227454                 10138      2534.0880   
7840  490212229

In [22]:
x_train_new = temp4.drop(['API','Liquid'], axis=1)
x_train_new

LATERAL_LENGTH_BLEND  PROP_PER_FOOT  WATER_PER_FOOT       GOR_30  \
0                     4358       760.4881        934.0413  2841.940260   
1                     4208       611.6503        546.6923  2420.241440   
2                     3983         0.0000          0.0000  2076.526858   
3                     4221       801.2611        505.2079  3652.173913   
4                     4027         0.0000          0.0000  2457.326098   
5                     8190      1408.8110          0.0000  1598.716588   
6                     4315         0.0000          0.0000  1407.787232   
7                     4053      3401.1990       2065.5310  1216.537860   
8                     3745      1742.2890       1807.3310  2059.910523   
9                     3866      1835.5640       1890.1990  3186.014597   
10                    4079      1568.7120       1630.7050  1654.373024   
11                    3262      1914.9830       1672.1780  2018.015596   
12                    3841      1738.0710       1281.4290  1905.849582   
13                    3787         0.0000          0.0000  1322.132647   
14                    9005       994.6866        591.8004  1249.318351   
15                    6720      1876.9140       1618.9850  1214.378209   
16                    8545      1252.0050       1235.5770  1061.961113   
17                    3815      1876.9190       1047.6740  1308.664642   
18                    6440       875.3403       1035.7760  2729.685603   
19                    8540      1369.7750       1313.5470  2009.318579   
20                    3554      1365.6510       1012.7990   498.804543   
21                    4012         0.0000          0.0000  3247.303236   
22                    3508       834.5635        651.6735  3074.136764   
23                    4589       221.6403        131.7694  2099.389996   
24                    4173       782.5092        594.7244  3173.713704   
25                    2550         0.0000        801.4464   605.031447   
26                    4105      1178.6280        807.1788  1976.423416   
27                    4038       651.1269        526.2178  2034.171413   
28                    8813       875.0183        464.8092  3757.302405   
29                    3902         0.0000          0.0000  3007.571259   
...                    ...            ...             ...          ...   
7814                  9434       646.8029          0.0000   330.741734   
7815                  9678       639.8415          0.0000   418.323704   
7816                  8897      1316.9290        662.2171   607.470289   
7817                  9341      1312.9230        849.5093   694.357309   
7818                  9642       613.0061          0.0000   569.349788   
7819                  6647      1172.1610        674.7793  1139.989029   
7820                  4059      1198.5090          0.0000   692.955112   
7821                  9014      1350.5770        838.8643   809.819371   
7822                  9445      1296.2060        812.3987  1169.257483   
7823                  8930      1398.2330        879.5729   495.476819   
7824                  9457      1307.2390        835.6952   843.114626   
7825                  9480      1077.4830        847.9736   611.024075   
7826                  8971      2424.1120       1348.6120   609.965988   
7827                  8627      2391.5970       1441.0970   454.680978   
7828                  9382      2143.3760       1241.4700   609.038127   
7829                  9710       562.3441          0.0000   534.401136   
7830                  9684       584.5623          0.0000   556.290893   
7831                  4714       552.4348          0.0000   543.292103   
7832                  4779       266.3333          0.0000   397.645115   
7833                  9784       543.0637          0.0000   587.270156   
7834                  1659       522.7615          0.0000   495.260664   
7835                  9705      1297.6180        876.0724   674.773118   
7836      

In [23]:
x_train_new = np.array(x_train_new)
print(x_train_new.shape,y_train.shape)

(7844, 16) (7844, 1)


In [24]:
# creating new model
model = Sequential()
model.add(Dense(output_dim=10, activation='relu', input_dim=x_train_new.shape[1]))
model.add(Dense(output_dim=5, activation='relu'))
# model.add(Dense(output_dim=3, activation='relu'))
model.add(Dense(output_dim=y_train.shape[1], activation='relu'))
adam = Adam(lr=0.01)
model.compile(loss='mae', optimizer=adam)

c:\users\gigabyte\appdata\local\programs\python\python37\lib\site-packages\ipykernel_launcher.py:3: UserWarning: Update your `Dense` call to the Keras 2 API: `Dense(activation="relu", input_dim=16, units=10)`
  This is separate from the ipykernel package so we can avoid doing imports until
c:\users\gigabyte\appdata\local\programs\python\python37\lib\site-packages\ipykernel_launcher.py:4: UserWarning: Update your `Dense` call to the Keras 2 API: `Dense(activation="relu", units=5)`
  after removing the cwd from sys.path.
c:\users\gigabyte\appdata\local\programs\python\python37\lib\site-packages\ipykernel_launcher.py:6: UserWarning: Update your `Dense` call to the Keras 2 API: `Dense(activation="relu", units=1)`
  


In [41]:
# fitting the model
model.fit(x_train_new,y_train,batch_size = 512, epochs= 20000 , verbose = 1,shuffle = True)

Epoch 1/20000
7844/7844 [==============================] - 0s 47us/step - loss: 126164.8055
Epoch 2/20000
7844/7844 [==============================] - 0s 2us/step - loss: 116354.6099
Epoch 3/20000
7844/7844 [==============================] - 0s 2us/step - loss: 93191.8561
Epoch 4/20000
7844/7844 [==============================] - 0s 2us/step - loss: 64880.8871
Epoch 5/20000
7844/7844 [==============================] - 0s 2us/step - loss: 51231.6113
Epoch 6/20000
7844/7844 [==============================] - 0s 2us/step - loss: 50831.1552
Epoch 7/20000
7844/7844 [==============================] - 0s 2us/step - loss: 50207.9343
Epoch 8/20000
7844/7844 [==============================] - 0s 2us/step - loss: 49845.1415
Epoch 9/20000
7844/7844 [==============================] - 0s 2us/step - loss: 49636.0789
Epoch 10/20000
7844/7844 [==============================] - 0s 2us/step - loss: 49484.9713
Epoch 11/20000
7844/7844 [==============================] - 0s 2us/step - loss: 49310.6762
Epoch

7844/7844 [==============================] - 0s 2us/step - loss: 45210.4579
Epoch 92/20000
7844/7844 [==============================] - 0s 2us/step - loss: 45150.1451
Epoch 93/20000
7844/7844 [==============================] - 0s 3us/step - loss: 45182.0380
Epoch 94/20000
7844/7844 [==============================] - 0s 2us/step - loss: 45154.2647
Epoch 95/20000
7844/7844 [==============================] - 0s 2us/step - loss: 45051.6301
Epoch 96/20000
7844/7844 [==============================] - 0s 2us/step - loss: 45034.1107
Epoch 97/20000
7844/7844 [==============================] - 0s 3us/step - loss: 45073.6957
Epoch 98/20000
7844/7844 [==============================] - 0s 2us/step - loss: 45244.1304
Epoch 99/20000
7844/7844 [==============================] - 0s 2us/step - loss: 45140.2540
Epoch 100/20000
7844/7844 [==============================] - 0s 2us/step - loss: 45004.7127
Epoch 101/20000
7844/7844 [==============================] - 0s 2us/step - loss: 44879.6801
Epoch 102/20

7844/7844 [==============================] - 0s 2us/step - loss: 43139.5562
Epoch 270/20000
7844/7844 [==============================] - 0s 3us/step - loss: 43215.8696
Epoch 271/20000
7844/7844 [==============================] - 0s 3us/step - loss: 43162.1964
Epoch 272/20000
7844/7844 [==============================] - 0s 2us/step - loss: 43303.0346
Epoch 273/20000
7844/7844 [==============================] - 0s 3us/step - loss: 43138.4646
Epoch 274/20000
7844/7844 [==============================] - 0s 2us/step - loss: 43075.6883
Epoch 275/20000
7844/7844 [==============================] - 0s 2us/step - loss: 43067.5018
Epoch 276/20000
7844/7844 [==============================] - 0s 2us/step - loss: 43053.8297
Epoch 277/20000
7844/7844 [==============================] - 0s 2us/step - loss: 43225.2237
Epoch 278/20000
7844/7844 [==============================] - 0s 2us/step - loss: 43234.4320
Epoch 279/20000
7844/7844 [==============================] - 0s 2us/step - loss: 43050.6153
Epoc

7844/7844 [==============================] - 0s 3us/step - loss: 42945.5776
Epoch 448/20000
7844/7844 [==============================] - 0s 3us/step - loss: 42553.9641
Epoch 449/20000
7844/7844 [==============================] - 0s 2us/step - loss: 42720.8629
Epoch 450/20000
7844/7844 [==============================] - 0s 3us/step - loss: 42662.0079
Epoch 451/20000
7844/7844 [==============================] - 0s 2us/step - loss: 42584.8118
Epoch 452/20000
7844/7844 [==============================] - 0s 2us/step - loss: 42591.8025
Epoch 453/20000
7844/7844 [==============================] - 0s 2us/step - loss: 42510.4381
Epoch 454/20000
7844/7844 [==============================] - 0s 2us/step - loss: 42538.0253
Epoch 455/20000
7844/7844 [==============================] - 0s 2us/step - loss: 42448.2880
Epoch 456/20000
7844/7844 [==============================] - 0s 2us/step - loss: 42629.1973
Epoch 457/20000
7844/7844 [==============================] - 0s 2us/step - loss: 42603.0741
Epoc

7844/7844 [==============================] - 0s 3us/step - loss: 42163.9809
Epoch 626/20000
7844/7844 [==============================] - 0s 2us/step - loss: 42121.7746
Epoch 627/20000
7844/7844 [==============================] - 0s 3us/step - loss: 42203.0437
Epoch 628/20000
7844/7844 [==============================] - 0s 2us/step - loss: 42048.1195
Epoch 629/20000
7844/7844 [==============================] - 0s 2us/step - loss: 42129.5887
Epoch 630/20000
7844/7844 [==============================] - 0s 2us/step - loss: 42560.4685
Epoch 631/20000
7844/7844 [==============================] - 0s 2us/step - loss: 42400.5272
Epoch 632/20000
7844/7844 [==============================] - 0s 2us/step - loss: 42349.6564
Epoch 633/20000
7844/7844 [==============================] - 0s 2us/step - loss: 42037.2517
Epoch 634/20000
7844/7844 [==============================] - 0s 2us/step - loss: 42112.6559
Epoch 635/20000
7844/7844 [==============================] - 0s 2us/step - loss: 42352.3608
Epoc

...

7844/7844 [==============================] - 0s 2us/step - loss: 39600.4840
Epoch 19179/20000
7844/7844 [==============================] - 0s 3us/step - loss: 39493.5249
Epoch 19180/20000
7844/7844 [==============================] - 0s 2us/step - loss: 39446.8244
Epoch 19181/20000
7844/7844 [==============================] - 0s 2us/step - loss: 40009.5585
Epoch 19182/20000
7844/7844 [==============================] - 0s 2us/step - loss: 39831.2583
Epoch 19183/20000
7844/7844 [==============================] - 0s 2us/step - loss: 39727.3814
Epoch 19184/20000
7844/7844 [==============================] - 0s 3us/step - loss: 39945.2595
Epoch 19185/20000
7844/7844 [==============================] - 0s 2us/step - loss: 39642.7780
Epoch 19186/20000
7844/7844 [==============================] - 0s 2us/step - loss: 39744.4362
Epoch 19187/20000
7844/7844 [==============================] - 0s 2us/step - loss: 39558.8264
Epoch 19188/20000
7844/7844 [==============================] - 0s 3us/step - l

7844/7844 [==============================] - 0s 2us/step - loss: 39623.3919
Epoch 19353/20000
7844/7844 [==============================] - 0s 3us/step - loss: 39483.4775
Epoch 19354/20000
7844/7844 [==============================] - 0s 2us/step - loss: 39511.0030
Epoch 19355/20000
7844/7844 [==============================] - 0s 3us/step - loss: 39420.3054
Epoch 19356/20000
7844/7844 [==============================] - 0s 2us/step - loss: 39400.7436
Epoch 19357/20000
7844/7844 [==============================] - 0s 2us/step - loss: 39444.8074
Epoch 19358/20000
7844/7844 [==============================] - 0s 2us/step - loss: 39474.3800
Epoch 19359/20000
7844/7844 [==============================] - 0s 2us/step - loss: 39643.4758
Epoch 19360/20000
7844/7844 [==============================] - 0s 2us/step - loss: 39732.3867
Epoch 19361/20000
7844/7844 [==============================] - 0s 2us/step - loss: 39753.9517
Epoch 19362/20000
7844/7844 [==============================] - 0s 3us/step - l

7844/7844 [==============================] - 0s 3us/step - loss: 39492.1337
Epoch 19527/20000
7844/7844 [==============================] - 0s 2us/step - loss: 39739.6230
Epoch 19528/20000
7844/7844 [==============================] - 0s 3us/step - loss: 39468.1990
Epoch 19529/20000
7844/7844 [==============================] - 0s 2us/step - loss: 39523.1582
Epoch 19530/20000
7844/7844 [==============================] - 0s 3us/step - loss: 39523.7951
Epoch 19531/20000
7844/7844 [==============================] - 0s 2us/step - loss: 39532.0848
Epoch 19532/20000
7844/7844 [==============================] - 0s 2us/step - loss: 39559.6439
Epoch 19533/20000
7844/7844 [==============================] - 0s 2us/step - loss: 39593.9676
Epoch 19534/20000
7844/7844 [==============================] - 0s 2us/step - loss: 39490.8165
Epoch 19535/20000
7844/7844 [==============================] - 0s 3us/step - loss: 39566.8958
Epoch 19536/20000
7844/7844 [==============================] - 0s 2us/step - l

7844/7844 [==============================] - 0s 3us/step - loss: 39639.6592
Epoch 19701/20000
7844/7844 [==============================] - 0s 2us/step - loss: 39532.6850
Epoch 19702/20000
7844/7844 [==============================] - 0s 3us/step - loss: 39426.0611
Epoch 19703/20000
7844/7844 [==============================] - 0s 2us/step - loss: 39497.2280
Epoch 19704/20000
7844/7844 [==============================] - 0s 3us/step - loss: 39511.5065
Epoch 19705/20000
7844/7844 [==============================] - 0s 3us/step - loss: 39428.9703
Epoch 19706/20000
7844/7844 [==============================] - 0s 2us/step - loss: 39512.8892
Epoch 19707/20000
7844/7844 [==============================] - 0s 3us/step - loss: 39413.9653
Epoch 19708/20000
7844/7844 [==============================] - 0s 2us/step - loss: 39571.0820
Epoch 19709/20000
7844/7844 [==============================] - 0s 3us/step - loss: 39511.4156
Epoch 19710/20000
7844/7844 [==============================] - 0s 2us/step - l

7844/7844 [==============================] - 0s 3us/step - loss: 39643.4415
Epoch 19875/20000
7844/7844 [==============================] - 0s 3us/step - loss: 39414.5459
Epoch 19876/20000
7844/7844 [==============================] - 0s 2us/step - loss: 39461.2276
Epoch 19877/20000
7844/7844 [==============================] - 0s 3us/step - loss: 39480.1560
Epoch 19878/20000
7844/7844 [==============================] - 0s 2us/step - loss: 39443.2313
Epoch 19879/20000
7844/7844 [==============================] - 0s 2us/step - loss: 39513.3262
Epoch 19880/20000
7844/7844 [==============================] - 0s 2us/step - loss: 39409.2989
Epoch 19881/20000
7844/7844 [==============================] - 0s 3us/step - loss: 39494.4108
Epoch 19882/20000
7844/7844 [==============================] - 0s 2us/step - loss: 39483.6067
Epoch 19883/20000
7844/7844 [==============================] - 0s 2us/step - loss: 39480.8136
Epoch 19884/20000
7844/7844 [==============================] - 0s 2us/step - l

In [25]:
# trying SVM Regressor
clf = svm.SVR()
clf.fit(x_train_new,y_train)

c:\users\gigabyte\appdata\local\programs\python\python37\lib\site-packages\sklearn\utils\validation.py:761: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
c:\users\gigabyte\appdata\local\programs\python\python37\lib\site-packages\sklearn\svm\base.py:196: FutureWarning: The default value of gamma will change from 'auto' to 'scale' in version 0.22 to account better for unscaled features. Set gamma explicitly to 'auto' or 'scale' to avoid this warning.
  "avoid this warning.", FutureWarning)


SVR(C=1.0, cache_size=200, coef0=0.0, degree=3, epsilon=0.1,
  gamma='auto_deprecated', kernel='rbf', max_iter=-1, shrinking=True,
  tol=0.001, verbose=False)

In [26]:
clf.score(x_train_new,y_train)

-0.03420949054774236

In [24]:
# trying to use the  productions of the first 3 months after the peak in the feature set
temp11 = production_data_train[production_data_train["Index"]<=3]
first_3_months_production = temp11.groupby("API").agg({'Liquid':'sum'})
first_3_months_production

Liquid
API                   
05001097720000   23586
05001097780100   23041
05001097800000    3666
05001097820000    3074
05001097830000    4004
05001098050100   48209
05001098450000   49613
05005071800000   42086
05005071890100   31255
05005071920000   31855
05005072090000   40891
05005072120000   16501
05005072140100   14172
05005072150100   18988
05005072170100   51475
05005072190100   60992
05005072210000   66894
05005072220000   25381
05005072250100   37079
05005072260000   57438
05123315730000    6087
05123331840000    5234
05123334240100    6432
05123349460000   32426
05123349600000   20555
05123349910100    1627
05123350610000   17340
05123350770000   19191
05123352460000    9941
05123352590000   14966
...                ...
49021211170000   46106
49021211180000   29323
49021211280000   56979
49021211310000   56199
49021211320000   12407
49021211460000   21859
49021211760000    7745
49021211780000   59883
49021211800000   70006
49021211820000   53206
49021212030000   40667
49021212280000   60882
49021212460000   56849
49021212470000   54970
49021212490000   63530
49021213620000   28083
49021213990000   36692
49021214000000    6637
49021214010000    9611
49021215910000   17070
49021217890000   12181
49021219480000   40322
49021221450000   26204
49021222690000   20407
49021222710000   16536
49021222940000   51215
49021222950000   56462
49021223030000   64818
49021226570000    6814
49021226580100    8839

[7844 rows x 1 columns]

In [25]:
temp5 = pd.merge(temp4,first_3_months_production,on='API',how = 'left')
temp5

API  Liquid_x  LATERAL_LENGTH_BLEND  PROP_PER_FOOT  \
0     05001097720000     65412                  4358       760.4881   
1     05001097780100     84043                  4208       611.6503   
2     05001097800000     13471                  3983         0.0000   
3     05001097820000     12992                  4221       801.2611   
4     05001097830000     15195                  4027         0.0000   
5     05001098050100    176206                  8190      1408.8110   
6     05001098450000    180189                  4315         0.0000   
7     05005071800000    126323                  4053      3401.1990   
8     05005071890100     66150                  3745      1742.2890   
9     05005071920000    186252                  3866      1835.5640   
10    05005072090000    142882                  4079      1568.7120   
11    05005072120000     62652                  3262      1914.9830   
12    05005072140100     63836                  3841      1738.0710   
13    05005072150100     99022                  3787         0.0000   
14    05005072170100    234552                  9005       994.6866   
15    05005072190100    264294                  6720      1876.9140   
16    05005072210000    250013                  8545      1252.0050   
17    05005072220000    102986                  3815      1876.9190   
18    05005072250100    200616                  6440       875.3403   
19    05005072260000    217756                  8540      1369.7750   
20    05123315730000     20563                  3554      1365.6510   
21    05123331840000     17377                  4012         0.0000   
22    05123334240100     20788                  3508       834.5635   
23    05123349460000     91506                  4589       221.6403   
24    05123349600000     76262                  4173       782.5092   
25    05123349910100      7703                  2550         0.0000   
26    05123350610000     70095                  4105      1178.6280   
27    05123350770000     91265                  4038       651.1269   
28    05123352460000     28831                  8813       875.0183   
29    05123352590000     51454                  3902         0.0000   
...              ...       ...                   ...            ...   
7814  49021211170000    180118                  9434       646.8029   
7815  49021211180000    133436                  9678       639.8415   
7816  49021211280000    142229                  8897      1316.9290   
7817  49021211310000    201533                  9341      1312.9230   
7818  49021211320000     87110                  9642       613.0061   
7819  49021211460000     73927                  6647      1172.1610   
7820  49021211760000     31937                  4059      1198.5090   
7821  49021211780000    207008                  9014      1350.5770   
7822  49021211800000    236270                  9445      1296.2060   
7823  49021211820000    191163                  8930      1398.2330   
7824  49021212030000    146182                  9457      1307.2390   
7825  49021212280000    164647                  9480      1077.4830   
7826  49021212460000    222063                  8971      2424.1120   
7827  49021212470000    187938                  8627      2391.5970   
7828  49021212490000    236922                  9382      2143.3760   
7829  49021213620000     95972                  9710       562.3441   
7830  49021213990000     90304                  9684       584.5623   
7831  49021214000000     31496                  4714       552.4348   
7832  49021214010000     41765                  4779       266.3333   
7833  49021215910000     88956                  9784       543.0637   
7834  49021217890000     63698                  1659       522.7615   
7835  49021219480000    134031                  9705      1297.6180   
7836  49021221450000    161373                  9670       437.8219   
7837  49021222690000    106619                  9822       572.4443   
7838  49021222710000     71089           

In [51]:
x_train_new_2_dataframe = temp5.drop(['API','Liquid_x'], axis=1)
x_train_new_2_dataframe

LATERAL_LENGTH_BLEND  PROP_PER_FOOT  WATER_PER_FOOT       GOR_30  \
0                     4358       760.4881        934.0413  2841.940260   
1                     4208       611.6503        546.6923  2420.241440   
2                     3983         0.0000          0.0000  2076.526858   
3                     4221       801.2611        505.2079  3652.173913   
4                     4027         0.0000          0.0000  2457.326098   
5                     8190      1408.8110          0.0000  1598.716588   
6                     4315         0.0000          0.0000  1407.787232   
7                     4053      3401.1990       2065.5310  1216.537860   
8                     3745      1742.2890       1807.3310  2059.910523   
9                     3866      1835.5640       1890.1990  3186.014597   
10                    4079      1568.7120       1630.7050  1654.373024   
11                    3262      1914.9830       1672.1780  2018.015596   
12                    3841      1738.0710       1281.4290  1905.849582   
13                    3787         0.0000          0.0000  1322.132647   
14                    9005       994.6866        591.8004  1249.318351   
15                    6720      1876.9140       1618.9850  1214.378209   
16                    8545      1252.0050       1235.5770  1061.961113   
17                    3815      1876.9190       1047.6740  1308.664642   
18                    6440       875.3403       1035.7760  2729.685603   
19                    8540      1369.7750       1313.5470  2009.318579   
20                    3554      1365.6510       1012.7990   498.804543   
21                    4012         0.0000          0.0000  3247.303236   
22                    3508       834.5635        651.6735  3074.136764   
23                    4589       221.6403        131.7694  2099.389996   
24                    4173       782.5092        594.7244  3173.713704   
25                    2550         0.0000        801.4464   605.031447   
26                    4105      1178.6280        807.1788  1976.423416   
27                    4038       651.1269        526.2178  2034.171413   
28                    8813       875.0183        464.8092  3757.302405   
29                    3902         0.0000          0.0000  3007.571259   
...                    ...            ...             ...          ...   
7814                  9434       646.8029          0.0000   330.741734   
7815                  9678       639.8415          0.0000   418.323704   
7816                  8897      1316.9290        662.2171   607.470289   
7817                  9341      1312.9230        849.5093   694.357309   
7818                  9642       613.0061          0.0000   569.349788   
7819                  6647      1172.1610        674.7793  1139.989029   
7820                  4059      1198.5090          0.0000   692.955112   
7821                  9014      1350.5770        838.8643   809.819371   
7822                  9445      1296.2060        812.3987  1169.257483   
7823                  8930      1398.2330        879.5729   495.476819   
7824                  9457      1307.2390        835.6952   843.114626   
7825                  9480      1077.4830        847.9736   611.024075   
7826                  8971      2424.1120       1348.6120   609.965988   
7827                  8627      2391.5970       1441.0970   454.680978   
7828                  9382      2143.3760       1241.4700   609.038127   
7829                  9710       562.3441          0.0000   534.401136   
7830                  9684       584.5623          0.0000   556.290893   
7831                  4714       552.4348          0.0000   543.292103   
7832                  4779       266.3333          0.0000   397.645115   
7833                  9784       543.0637          0.0000   587.270156   
7834                  1659       522.7615          0.0000   495.260664   
7835                  9705      1297.6180        876.0724   674.773118   
7836      

In [27]:
x_train_new_2 = np.array(x_train_new_2_dataframe)
print(x_train_new_2.shape,y_train.shape)

(7844, 17) (7844, 1)


In [31]:
# creating new model
model = Sequential()
model.add(Dense(output_dim=10, activation='relu', input_dim=x_train_new_2.shape[1]))
model.add(Dense(output_dim=5, activation='relu'))
# model.add(Dense(output_dim=3, activation='relu'))
model.add(Dense(output_dim=y_train.shape[1], activation='relu'))
adam = Adam(lr=0.01)
model.compile(loss='mae', optimizer=adam)

c:\users\gigabyte\appdata\local\programs\python\python37\lib\site-packages\ipykernel_launcher.py:3: UserWarning: Update your `Dense` call to the Keras 2 API: `Dense(activation="relu", input_dim=17, units=10)`
  This is separate from the ipykernel package so we can avoid doing imports until
c:\users\gigabyte\appdata\local\programs\python\python37\lib\site-packages\ipykernel_launcher.py:4: UserWarning: Update your `Dense` call to the Keras 2 API: `Dense(activation="relu", units=5)`
  after removing the cwd from sys.path.
c:\users\gigabyte\appdata\local\programs\python\python37\lib\site-packages\ipykernel_launcher.py:6: UserWarning: Update your `Dense` call to the Keras 2 API: `Dense(activation="relu", units=1)`
  


In [32]:
model.fit(x_train_new_2,y_train,batch_size = 512, epochs= 20000 , verbose = 1,shuffle = True)

Epoch 1/20000
7844/7844 [==============================] - 0s 22us/step - loss: 106538.0276
Epoch 2/20000
7844/7844 [==============================] - 0s 2us/step - loss: 54643.1034
Epoch 3/20000
7844/7844 [==============================] - 0s 2us/step - loss: 33086.8078
Epoch 4/20000
7844/7844 [==============================] - 0s 2us/step - loss: 25671.0987
Epoch 5/20000
7844/7844 [==============================] - 0s 2us/step - loss: 24421.6891
Epoch 6/20000
7844/7844 [==============================] - 0s 2us/step - loss: 24247.2252
Epoch 7/20000
7844/7844 [==============================] - 0s 2us/step - loss: 24122.1562
Epoch 8/20000
7844/7844 [==============================] - 0s 2us/step - loss: 24070.8044
Epoch 9/20000
7844/7844 [==============================] - 0s 2us/step - loss: 24040.0377
Epoch 10/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23981.6233
Epoch 11/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23964.7966
Epoch 

7844/7844 [==============================] - 0s 2us/step - loss: 22856.0552
Epoch 92/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22898.3598
Epoch 93/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22837.6214
Epoch 94/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22849.9809
Epoch 95/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22831.3761
Epoch 96/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22862.7410
Epoch 97/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22837.5590
Epoch 98/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22832.5245
Epoch 99/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22910.0202
Epoch 100/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22949.1325
Epoch 101/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22892.0865
Epoch 102/20

7844/7844 [==============================] - 0s 2us/step - loss: 22649.2016
Epoch 181/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22681.3160
Epoch 182/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22580.0746
Epoch 183/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22599.2430
Epoch 184/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22637.3274
Epoch 185/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22618.1444
Epoch 186/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22526.5355
Epoch 187/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22537.0338
Epoch 188/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22637.1593
Epoch 189/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22614.7754
Epoch 190/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22589.3458
Epoc

7844/7844 [==============================] - 0s 2us/step - loss: 22449.4188
Epoch 270/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22469.9850
Epoch 271/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22526.0975
Epoch 272/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22542.9276
Epoch 273/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22393.2340
Epoch 274/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22425.6746
Epoch 275/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22387.7774
Epoch 276/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22402.0556
Epoch 277/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22367.8084
Epoch 278/20000
7844/7844 [==============================] - 0s 3us/step - loss: 22451.7196
Epoch 279/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22400.0873
Epoc

7844/7844 [==============================] - 0s 2us/step - loss: 22540.6328
Epoch 359/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22490.7103
Epoch 360/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22327.8519
Epoch 361/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22394.0048
Epoch 362/20000
7844/7844 [==============================] - 0s 3us/step - loss: 22305.8962
Epoch 363/20000
7844/7844 [==============================] - 0s 3us/step - loss: 22375.8811
Epoch 364/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22356.6071
Epoch 365/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22276.8183
Epoch 366/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22570.4018
Epoch 367/20000
7844/7844 [==============================] - 0s 3us/step - loss: 22429.0854
Epoch 368/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22584.4242
Epoc

7844/7844 [==============================] - 0s 2us/step - loss: 22175.8221
Epoch 448/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22233.3132
Epoch 449/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22177.6729
Epoch 450/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22163.9297
Epoch 451/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22135.6765
Epoch 452/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22147.0539
Epoch 453/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22142.8106
Epoch 454/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22217.3110
Epoch 455/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22554.2927
Epoch 456/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22219.0488
Epoch 457/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22364.0840
Epoc

7844/7844 [==============================] - 0s 2us/step - loss: 22241.5074
Epoch 537/20000
7844/7844 [==============================] - 0s 3us/step - loss: 22090.2018
Epoch 538/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22130.4521
Epoch 539/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22122.0756
Epoch 540/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22158.0248
Epoch 541/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22059.0263
Epoch 542/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22117.1505
Epoch 543/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22147.4771
Epoch 544/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22124.8793
Epoch 545/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22103.5122
Epoch 546/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22104.7725
Epoc

7844/7844 [==============================] - 0s 2us/step - loss: 22124.8858
Epoch 626/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22141.8467
Epoch 627/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22243.7732
Epoch 628/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22100.1886
Epoch 629/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22107.2127
Epoch 630/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22100.2618
Epoch 631/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22205.4962
Epoch 632/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22323.9675
Epoch 633/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22105.0212
Epoch 634/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22049.2152
Epoch 635/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22088.2513
Epoc

7844/7844 [==============================] - 0s 2us/step - loss: 22332.3056
Epoch 715/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22061.2724
Epoch 716/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22080.3738
Epoch 717/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22147.9003
Epoch 718/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22120.3377
Epoch 719/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22112.4507
Epoch 720/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22081.7007
Epoch 721/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22006.8303
Epoch 722/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22084.5831
Epoch 723/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22077.5577
Epoch 724/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22136.6767
Epoc

KeyboardInterrupt: 

In [33]:
# Reading the test files
production_data_test = pd.read_csv("production_data_test.csv",dtype={'API':str})
test_APIs = pd.read_csv("test_APIs.csv",dtype={'API':str})
production_data_test["API"] = production_data_test["API"].apply(fixAPI)
test_APIs["API"] = test_APIs["API"].apply(fixAPI)

In [34]:
# preprocessing the production_data_test files

In [35]:
# Removing the duplicates
start = time.time()
production_data_test = production_data_test.sort_values(['_LastUpdate'])
production_data_test.drop_duplicates(subset=['API','Year','Month'],keep='last',inplace=True)
end = time.time()
print('RemovingDuplicates',end-start)

RemovingDuplicates 0.018001079559326172


In [36]:
# Remove pre-peek month
start = time.time()
maxLiquid = production_data_test.groupby(['API'],as_index=False).agg({'Liquid':'max'})
maxDate = pd.merge(maxLiquid[['API','Liquid']],production_data_test[['API','Liquid','Year','Month']],on=['API','Liquid'],how='left')

max1 = maxDate.groupby(['API','Liquid'],as_index=False).agg({'Year':'min'})
maxDate = pd.merge(maxDate[['API','Liquid','Year','Month']],max1[['API','Liquid','Year']],on=['API','Liquid','Year'],how='right')
maxDate = maxDate.groupby(['API','Liquid','Year'],as_index=False).agg({'Month':'min'})

maxDate = maxDate[['API','Year','Month']]
maxDate = maxDate.rename(columns={"Year":"maxYear",'Month':'maxMonth'})
production_data_test = pd.merge(production_data_test,maxDate[['API','maxYear','maxMonth']],on='API')
production_data_test = production_data_test[((production_data_test['Year']-production_data_test['maxYear'])*12+production_data_test['Month']-production_data_test['maxMonth'])>=0]

end = time.time()
print('RemovePrePeekMonth',end-start)

RemovePrePeekMonth 0.05100297927856445


In [37]:
# Adding Index
start = time.time()
production_data_test["Index"] = (production_data_test["Year"]-production_data_test['maxYear'])*12+production_data_test["Month"]-production_data_test["maxMonth"]+1
end = time.time()
print('IndexColumn',end-start)

IndexColumn 0.0740041732788086


In [38]:
production_data_test

API  Year  Month  Liquid    Gas  RatioGasOil  Water  \
0      33053055910300  2014      9   27613  43459     1.573860  23206   
1      33053055910300  2014     10   15241  21214     1.391903  11540   
2      33053055910300  2014     11    6201   8077     1.302532   4418   
3      33053055910300  2014     12   11948  23865     1.997405   9443   
4      33053055910300  2015      1   12251  34407     2.808505   9640   
5      33053051930000  2015     10    1766   3371     1.908834   1354   
6      33053051930000  2015      9    1797   3236     1.800779   1345   
7      33053051930000  2015      8    1947   3570     1.833590   1338   
8      33053051930000  2015      6    2185   4143     1.896110   1719   
9      33053051930000  2015      5    2501   3128     1.250700   1404   
10     33053051930000  2015      4    2061   2875     1.394954   1565   
11     33053051930000  2015      3    2865   5076     1.771728   2068   
12     33053051930000  2015      2    2863   5463     1.908138   1634   
13     33053051930000  2015      7    2014   3803     1.888282   1353   
14     33053051930000  2014     12    3841   5331     1.387920   2545   
15     33053051930000  2014     11    4219   5947     1.409576   2459   
16     33053051930000  2014     10    4801   5932     1.235576   4859   
17     33053051930000  2014      9    3643   4776     1.311007   2444   
18     33053051930000  2014      8    3748   6958     1.856457   2773   
19     33053051930000  2014      7    1624   2949     1.815887   1357   
20     33053051930000  2014      6    7343   8167     1.112216   5083   
21     33053051930000  2014      5   11933   8585     0.719434   7960   
22     33053051930000  2015      1    3467   5288     1.525238   1453   
23     33053051930000  2016      6    1932   3276     1.695652   1725   
24     33053051930000  2018      3    1846   1686     0.913326    752   
25     05123380260000  2014     10    9220  21928     2.378308   3065   
26     05123380260000  2014      8   10633  18411     1.731496      0   
27     05123380260000  2014      9   10291  21270     2.066855      0   
29     33053060610000  2015      7   29874  55713     1.864933   1775   
30     33053060610000  2015      8   20034  47974     2.394629   1558   
...               ...   ...    ...     ...    ...          ...    ...   
19269  42105419820000  2014      7    3623  21195     5.850124  17055   
19270  42105418860000  2014      8    1529  12642     8.268149   2623   
19271  42105418860000  2014      9    1383  14886    10.763557   2500   
19273  42105418860000  2014      1    1738  20952    12.055236      0   
19274  42105418860000  2014      7    1476  16081    10.894986      0   
19275  42105418860000  2014      3    1231  24241    19.692120      0   
19276  42105418860000  2014      6    1414  20516    14.509194      0   
19277  42105418860000  2014      5    1460  26126    17.894521      0   
19278  42105418860000  2014      4    1337  26944    20.152580      0   
19279  42105420950000  2015      1    5334  31760     5.954256  12991   
19280  42105420950000  2015      3    5274  33621     6.374858  11867   
19281  42105420120000  2014     11    1521   5468     3.595003  11566   
19282  42105420120000  2014     10    1687   5397     3.199170  13290   
19283  42105420120000  2014     12    1566   5204     3.323116  11397   
19284  42105420120000  2014      9    1961   4579     2.335033  16467   
19285  42105420050000  2014      9    5160  25489     4.939729  15110   
19286  42105420050000  2014     10    4306  24229     5.626800  12180   
19287  42105420050000  2014     11    3747  20728     5.531892  10584   
19288  42105419990000  2014      8    5467  14440     2.641302  22159   
19289  42105419990000  2014      7    6137  12635     2.058824  24688   
19290  42105419990000  2014      6    6830  10752     1.574231  27204   
19291  42105419960000  2014      7    4544   8768     1.929577  24480   
19292  42105419960000  2014      8    4069  10032     2.465471  21876   
192

In [39]:
temp12 = production_data_test[production_data_test["Index"]<=3]
first_3_months_production_test = temp12.groupby("API").agg({'Liquid':'sum'})
first_3_months_production_test

Liquid
API                   
05001097740200   20913
05001097770000   28747
05001097790000   34025
05001097810000    4090
05001097850100    3546
05001098010100   21708
05001098260100   20621
05005072030100   12764
05005072180000   60026
05005072200000   52919
05005072230000   72049
05005072240000   63126
05123340180000   22057
05123343840000   20290
05123346950000   10504
05123349520000   28823
05123352520000   17483
05123352980000   24305
05123353520000   15037
05123355430000   13018
05123358360000   16573
05123359980000   17874
05123360020000   30990
05123360790000   11663
05123360830000   14448
05123361210000   21066
05123362020000   15038
05123362100000   20760
05123362310000   36098
05123362780000   19748
...                ...
42495336180000   55997
42495336790000   37825
49021210080000   10427
49021210290000    4989
49021210300000   20234
49021210520000   11984
49021210540000    9992
49021210570000   57887
49021210640000   48324
49021210660000   29782
49021210790000   64200
49021210830000   73399
49021211290000   23765
49021211330000   17396
49021211350000   44117
49021211360000   23859
49021211400000   54397
49021211430000   39008
49021211640000   33541
49021211810000   65383
49021212260000   62865
49021212270000   52327
49021213980000   23987
49021215690000   36548
49021215700000   37552
49021215920000   18913
49021221440000   11864
49021222720000    8948
49021222750000   17514
49021222980000   66721

[3463 rows x 1 columns]

In [40]:
temp111 = pd.merge(first_3_months_production_test,Harmony_data,on='API',how = 'left')
temp111

API  Liquid  LATERAL_LENGTH_BLEND  PROP_PER_FOOT  \
0     05001097740200   20913                  3993            NaN   
1     05001097770000   28747                  4314            NaN   
2     05001097790000   34025                  3815      2025.4990   
3     05001097810000    4090                  3977            NaN   
4     05001097850100    3546                  3974            NaN   
5     05001098010100   21708                  4276       983.2365   
6     05001098260100   20621                  5395            NaN   
7     05005072030100   12764                  3988      1727.1980   
8     05005072180000   60026                  8950      1975.4250   
9     05005072200000   52919                  6790      1333.9630   
10    05005072230000   72049                  6370      1418.4980   
11    05005072240000   63126                  8820      1301.5820   
12    05123340180000   22057                  5760      1028.5570   
13    05123343840000   20290                  3926      1158.6060   
14    05123346950000   10504                  4233       315.7228   
15    05123349520000   28823                  6506      1401.7150   
16    05123352520000   17483                  3970            NaN   
17    05123352980000   24305                  4145       904.9650   
18    05123353520000   15037                  3873            NaN   
19    05123355430000   13018                  3201      1867.0150   
20    05123358360000   16573                  3899      1010.1350   
21    05123359980000   17874                  4302       962.2211   
22    05123360020000   30990                  6623       797.8011   
23    05123360790000   11663                  4735       699.5160   
24    05123360830000   14448                  4376       872.2310   
25    05123361210000   21066                  7066       820.8480   
26    05123362020000   15038                  4245       312.2728   
27    05123362100000   20760                  4113      1648.1310   
28    05123362310000   36098                  6736       534.8922   
29    05123362780000   19748                  3802            NaN   
...              ...     ...                   ...            ...   
3433  42495336180000   55997                  4300      1560.2750   
3434  42495336790000   37825                  4140      1530.2830   
3435  49021210080000   10427                  4709       406.0006   
3436  49021210290000    4989                  4172       392.9701   
3437  49021210300000   20234                  8776       451.8998   
3438  49021210520000   11984                  4200       975.0823   
3439  49021210540000    9992                  4086       993.4370   
3440  49021210570000   57887                  9114      1274.3590   
3441  49021210640000   48324                  9450      1461.4580   
3442  49021210660000   29782                  6906      1076.8060   
3443  49021210790000   64200                  8976      1878.1840   
3444  49021210830000   73399                  9431      1249.7340   
3445  49021211290000   23765                  6599      1134.2740   
3446  49021211330000   17396                  9690       611.8026   
3447  49021211350000   44117                  9113      1185.2040   
3448  49021211360000   23859                  6587      1507.0010   
3449  49021211400000   54397                  8629      2432.7480   
3450  49021211430000   39008                  9457      1300.0010   
3451  49021211640000   33541                  9696       572.8765   
3452  49021211810000   65383                  7291      1999.2230   
3453  49021212260000   62865                  9139      1213.1360   
3454  49021212270000   52327                  9488      1285.5550   
3455  49021213980000   23987                  9714       519.6845   
3456  49021215690000   36548                  9739      1326.9110   
3457  49021215700000   37552                  9313      1129.7460   
3458  49021215920000   18913                  9802       579.4500   
3459  490212214

In [41]:
temp112 = pd.merge(temp111,temp3,on='API',how = 'left')
temp112.fillna(0,inplace = True)
temp112

API  Liquid  LATERAL_LENGTH_BLEND  PROP_PER_FOOT  \
0     05001097740200   20913                  3993         0.0000   
1     05001097770000   28747                  4314         0.0000   
2     05001097790000   34025                  3815      2025.4990   
3     05001097810000    4090                  3977         0.0000   
4     05001097850100    3546                  3974         0.0000   
5     05001098010100   21708                  4276       983.2365   
6     05001098260100   20621                  5395         0.0000   
7     05005072030100   12764                  3988      1727.1980   
8     05005072180000   60026                  8950      1975.4250   
9     05005072200000   52919                  6790      1333.9630   
10    05005072230000   72049                  6370      1418.4980   
11    05005072240000   63126                  8820      1301.5820   
12    05123340180000   22057                  5760      1028.5570   
13    05123343840000   20290                  3926      1158.6060   
14    05123346950000   10504                  4233       315.7228   
15    05123349520000   28823                  6506      1401.7150   
16    05123352520000   17483                  3970         0.0000   
17    05123352980000   24305                  4145       904.9650   
18    05123353520000   15037                  3873         0.0000   
19    05123355430000   13018                  3201      1867.0150   
20    05123358360000   16573                  3899      1010.1350   
21    05123359980000   17874                  4302       962.2211   
22    05123360020000   30990                  6623       797.8011   
23    05123360790000   11663                  4735       699.5160   
24    05123360830000   14448                  4376       872.2310   
25    05123361210000   21066                  7066       820.8480   
26    05123362020000   15038                  4245       312.2728   
27    05123362100000   20760                  4113      1648.1310   
28    05123362310000   36098                  6736       534.8922   
29    05123362780000   19748                  3802         0.0000   
...              ...     ...                   ...            ...   
3433  42495336180000   55997                  4300      1560.2750   
3434  42495336790000   37825                  4140      1530.2830   
3435  49021210080000   10427                  4709       406.0006   
3436  49021210290000    4989                  4172       392.9701   
3437  49021210300000   20234                  8776       451.8998   
3438  49021210520000   11984                  4200       975.0823   
3439  49021210540000    9992                  4086       993.4370   
3440  49021210570000   57887                  9114      1274.3590   
3441  49021210640000   48324                  9450      1461.4580   
3442  49021210660000   29782                  6906      1076.8060   
3443  49021210790000   64200                  8976      1878.1840   
3444  49021210830000   73399                  9431      1249.7340   
3445  49021211290000   23765                  6599      1134.2740   
3446  49021211330000   17396                  9690       611.8026   
3447  49021211350000   44117                  9113      1185.2040   
3448  49021211360000   23859                  6587      1507.0010   
3449  49021211400000   54397                  8629      2432.7480   
3450  49021211430000   39008                  9457      1300.0010   
3451  49021211640000   33541                  9696       572.8765   
3452  49021211810000   65383                  7291      1999.2230   
3453  49021212260000   62865                  9139      1213.1360   
3454  49021212270000   52327                  9488      1285.5550   
3455  49021213980000   23987                  9714       519.6845   
3456  49021215690000   36548                  9739      1326.9110   
3457  49021215700000   37552                  9313      1129.7460   
3458  49021215920000   18913                  9802       579.4500   
3459  490212214

In [42]:
x_test_dataframe = pd.merge(test_APIs,temp112,on='API',how = 'left')
x_test_dataframe

API  Liquid  LATERAL_LENGTH_BLEND  PROP_PER_FOOT  \
0     33025022600000   64501                  9573       499.6697   
1     33053059470100   54321                  7857       599.2208   
2     33053055610000   53829                  9555       367.4926   
3     33025015390100   34667                 12573         0.0000   
4     33061031960000   41628                  9719       925.8431   
5     33053045380000  109641                 10873       491.1978   
6     33053047860000   82903                  8441       963.6350   
7     33105040050000   96266                  9717       658.2175   
8     33025025710000   36848                  9621       445.0131   
9     33053060710000   33885                  9505       427.1875   
10    33061034360000   66979                  9467      1843.8870   
11    33053066930000   56176                  9678      1010.1250   
12    33053053880100   14389                  9480       213.9955   
13    33105035790000   15980                  9843       292.8173   
14    33023012680000    8740                  9346       284.8910   
15    33053052320000   36618                 10230       381.1479   
16    33053038370000   50831                  9653       303.7492   
17    33105036810000   53973                 10339       328.4052   
18    33061029220000   40391                  3820      1405.4300   
19    33053052690100   54652                  7956       318.4861   
20    33053054980000   40525                  9493       368.9908   
21    33023011460000   18900                  9718       454.1488   
22    33061028540000   57903                  8981      1292.8200   
23    33053052150000   68356                  9787      1007.7240   
24    33025023950000   62957                  9444       510.1711   
25    33061028590000   67712                  6161      1473.1020   
26    33053045360000   77252                 10799       495.4203   
27    33007018020200    5108                  6163       272.2891   
28    33023013070000   17214                  9448       293.4908   
29    33105036510000   29615                 10196       588.7379   
...              ...     ...                   ...            ...   
3301  42389339860000   37989                  4302      1195.2750   
3302  30015421400000   35505                  3646       602.6765   
3303  42301321540000   32953                  4115      1169.7200   
3304  42235359010000   28023                  8796       920.8578   
3305  42301323360000   33982                  4156      1164.6840   
3306  42383382170000   16545                  6892       830.2496   
3307  42235355620000   23679                  7633      1209.2670   
3308  42389343100000   43528                  6664      4502.9820   
3309  42383381550100   27218                  7862       828.9055   
3310  42389335030000   25736                  4473      1735.7250   
3311  42389341290000   28575                  4472         0.0000   
3312  42383382200000   14029                  7622       780.2644   
3313  42383384050000   14813                  7862       784.0753   
3314  42383384770000   26406                  7222       981.5971   
3315  42389339210000   36850                  4547      1765.5820   
3316  42105420050000   13213                  7113      1185.2190   
3317  42389341030000   16954                  4024      1410.7090   
3318  42173371500000   29299                  9697      1160.9440   
3319  30015417870000    5181                  4468      1282.4090   
3320  42389340210000   75968                  4742      1115.9440   
3321  42301324010000   46699                  4663      1325.2410   
3322  42389339460000   30641                  4453       839.4534   
3323  42301324910000   62013                  4664      1333.2620   
3324  42301321610000   28026                  3547      1976.0930   
3325  42383388130000    4856                  4664      1011.3330   
3326  42235355700000   28377                  8282       900.9319   
3327  421093274

In [43]:
liquid_column = x_test_dataframe['Liquid']
x_test_dataframe = x_test_dataframe.drop(['API','Liquid'], axis=1)
x_test_dataframe['Liquid'] = liquid_column
x_test_dataframe

LATERAL_LENGTH_BLEND  PROP_PER_FOOT  WATER_PER_FOOT        GOR_30  \
0                     9573       499.6697        818.1763   1125.698608   
1                     7857       599.2208       1169.4620    818.737736   
2                     9555       367.4926        230.7927   1355.204295   
3                    12573         0.0000        411.8087   1233.374961   
4                     9719       925.8431        675.1400   2045.007289   
5                    10873       491.1978        330.7324   1135.133872   
6                     8441       963.6350        485.2353   1000.000000   
7                     9717       658.2175        764.0712   1531.587962   
8                     9621       445.0131        349.8394    949.591645   
9                     9505       427.1875        326.1827   2425.404716   
10                    9467      1843.8870        800.0212    419.585647   
11                    9678      1010.1250        551.6037   1796.345495   
12                    9480       213.9955        280.5808   1099.849937   
13                    9843       292.8173        243.5136    903.770311   
14                    9346       284.8910        257.1674    509.043174   
15                   10230       381.1479        904.9768    892.805127   
16                    9653       303.7492        279.5417   1762.111383   
17                   10339       328.4052        788.2121   1653.349876   
18                    3820      1405.4300       1214.8340    458.220038   
19                    7956       318.4861        835.8970   1433.863965   
20                    9493       368.9908        266.8858   1551.969519   
21                    9718       454.1488        257.7746   1289.889526   
22                    8981      1292.8200        991.9944    443.830828   
23                    9787      1007.7240        490.1945   1194.556937   
24                    9444       510.1711        547.7758   1165.888578   
25                    6161      1473.1020       1362.8640   1015.916634   
26                   10799       495.4203        910.8478   1116.567649   
27                    6163       272.2891        430.1466   1806.701031   
28                    9448       293.4908        254.4346    623.956234   
29                   10196       588.7379        305.0301   1230.010277   
...                    ...            ...             ...           ...   
3301                  4302      1195.2750       1401.9740   3194.424401   
3302                  3646       602.6765        786.1152    943.084857   
3303                  4115      1169.7200       1017.6820   2305.760963   
3304                  8796       920.8578        954.6122   2941.977800   
3305                  4156      1164.6840       1039.8280   1867.295141   
3306                  6892       830.2496        960.0714   1592.706570   
3307                  7633      1209.2670       1242.0280   1360.569872   
3308                  6664      4502.9820       1500.8250   1110.676509   
3309                  7862       828.9055       1038.3870    811.326206   
3310                  4473      1735.7250       1704.9300  12412.611718   
3311                  4472         0.0000          0.0000   1788.017705   
3312                  7622       780.2644        931.1846    502.276452   
3313                  7862       784.0753       1022.1620   1325.704225   
3314                  7222       981.5971       1330.8470   1050.013373   
3315                  4547      1765.5820       2868.9940    811.777655   
3316                  7113      1185.2190          0.0000   4712.068296   
3317                  4024      1410.7090       1561.0080   2077.545298   
3318                  9697      1160.9440       1471.0880   1336.915297   
3319                  4468      1282.4090        953.3336   1660.234321   
3320                  4742      1115.9440       1022.3230   1555.410957   
3321                  4663      1325.2410       1220.1900   5173.988571   
3322                  4453     

In [44]:
x_test = np.array(x_test_dataframe)
print(x_test_dataframe.shape)

(3331, 17)


In [45]:
prediction_output = model.predict(x_test)
prediction_output

array([[228082.61],
       [199968.27],
       [191962.98],
       ...,
       [ 73584.39],
       [221047.77],
       [228597.52]], dtype=float32)

In [46]:
prediction_output_series = pd.DataFrame(prediction_output)
prediction_output_series

0
0     228082.609375
1     199968.265625
2     191962.984375
3     143895.046875
4     160785.500000
5     359739.500000
6     277560.062500
7     317185.093750
8     145604.640625
9     128019.960938
10    241800.031250
11    201311.109375
12     72477.570312
13     79688.664062
14     50390.488281
15    153973.671875
16    178447.750000
17    207506.984375
18    149700.703125
19    195152.203125
20    161537.859375
21     93539.296875
22    215124.828125
23    237545.812500
24    222159.328125
25    235760.265625
26    272708.687500
27     26776.843750
28     86208.593750
29    127280.164062
...             ...
3301  148048.140625
3302  141535.546875
3303  129148.640625
3304   92454.726562
3305  127967.828125
3306   54309.308594
3307   90175.406250
3308  170388.015625
3309   96271.007812
3310  102076.687500
3311  109653.867188
3312   53155.484375
3313   50248.898438
3314  106374.570312
3315  162365.796875
3316   47890.343750
3317   72244.804688
3318  106517.867188
3319   30758.902344
3320  263547.625000
3321  181794.140625
3322  117066.937500
3323  229437.953125
3324  105248.906250
3325   21185.427734
3326   89930.476562
3327   51407.777344
3328   73584.390625
3329  221047.765625
3330  228597.515625

[3331 rows x 1 columns]

In [47]:
test_APIs

API
0     33025022600000
1     33053059470100
2     33053055610000
3     33025015390100
4     33061031960000
5     33053045380000
6     33053047860000
7     33105040050000
8     33025025710000
9     33053060710000
10    33061034360000
11    33053066930000
12    33053053880100
13    33105035790000
14    33023012680000
15    33053052320000
16    33053038370000
17    33105036810000
18    33061029220000
19    33053052690100
20    33053054980000
21    33023011460000
22    33061028540000
23    33053052150000
24    33025023950000
25    33061028590000
26    33053045360000
27    33007018020200
28    33023013070000
29    33105036510000
...              ...
3301  42389339860000
3302  30015421400000
3303  42301321540000
3304  42235359010000
3305  42301323360000
3306  42383382170000
3307  42235355620000
3308  42389343100000
3309  42383381550100
3310  42389335030000
3311  42389341290000
3312  42383382200000
3313  42383384050000
3314  42383384770000
3315  42389339210000
3316  42105420050000
3317  42389341030000
3318  42173371500000
3319  30015417870000
3320  42389340210000
3321  42301324010000
3322  42389339460000
3323  42301324910000
3324  42301321610000
3325  42383388130000
3326  42235355700000
3327  42109327420000
3328  42235359230000
3329  42301321840000
3330  42371071730300

[3331 rows x 1 columns]

In [48]:
predictions_dataframe = pd.DataFrame()
predictions_dataframe['Id'] = test_APIs['API']
predictions_dataframe['Predicted'] = prediction_output_series[0]
predictions_dataframe

Id      Predicted
0     33025022600000  228082.609375
1     33053059470100  199968.265625
2     33053055610000  191962.984375
3     33025015390100  143895.046875
4     33061031960000  160785.500000
5     33053045380000  359739.500000
6     33053047860000  277560.062500
7     33105040050000  317185.093750
8     33025025710000  145604.640625
9     33053060710000  128019.960938
10    33061034360000  241800.031250
11    33053066930000  201311.109375
12    33053053880100   72477.570312
13    33105035790000   79688.664062
14    33023012680000   50390.488281
15    33053052320000  153973.671875
16    33053038370000  178447.750000
17    33105036810000  207506.984375
18    33061029220000  149700.703125
19    33053052690100  195152.203125
20    33053054980000  161537.859375
21    33023011460000   93539.296875
22    33061028540000  215124.828125
23    33053052150000  237545.812500
24    33025023950000  222159.328125
25    33061028590000  235760.265625
26    33053045360000  272708.687500
27    33007018020200   26776.843750
28    33023013070000   86208.593750
29    33105036510000  127280.164062
...              ...            ...
3301  42389339860000  148048.140625
3302  30015421400000  141535.546875
3303  42301321540000  129148.640625
3304  42235359010000   92454.726562
3305  42301323360000  127967.828125
3306  42383382170000   54309.308594
3307  42235355620000   90175.406250
3308  42389343100000  170388.015625
3309  42383381550100   96271.007812
3310  42389335030000  102076.687500
3311  42389341290000  109653.867188
3312  42383382200000   53155.484375
3313  42383384050000   50248.898438
3314  42383384770000  106374.570312
3315  42389339210000  162365.796875
3316  42105420050000   47890.343750
3317  42389341030000   72244.804688
3318  42173371500000  106517.867188
3319  30015417870000   30758.902344
3320  42389340210000  263547.625000
3321  42301324010000  181794.140625
3322  42389339460000  117066.937500
3323  42301324910000  229437.953125
3324  42301321610000  105248.906250
3325  42383388130000   21185.427734
3326  42235355700000   89930.476562
3327  42109327420000   51407.777344
3328  42235359230000   73584.390625
3329  42301321840000  221047.765625
3330  42371071730300  228597.515625

[3331 rows x 2 columns]

In [49]:
predictions_dataframe.to_csv('Predictions.csv',index=False)

In [76]:
# x_train_new_3_dataframe = x_train_new_2_dataframe.drop(['CountyName','operatorNameIHS','formation','BasinName','StateName'], axis=1)
x_train_new_3_dataframe = x_train_new_2_dataframe
x_train_new_3_dataframe

LATERAL_LENGTH_BLEND  PROP_PER_FOOT  WATER_PER_FOOT       GOR_30  \
0                     4358       760.4881        934.0413  2841.940260   
1                     4208       611.6503        546.6923  2420.241440   
2                     3983         0.0000          0.0000  2076.526858   
3                     4221       801.2611        505.2079  3652.173913   
4                     4027         0.0000          0.0000  2457.326098   
5                     8190      1408.8110          0.0000  1598.716588   
6                     4315         0.0000          0.0000  1407.787232   
7                     4053      3401.1990       2065.5310  1216.537860   
8                     3745      1742.2890       1807.3310  2059.910523   
9                     3866      1835.5640       1890.1990  3186.014597   
10                    4079      1568.7120       1630.7050  1654.373024   
11                    3262      1914.9830       1672.1780  2018.015596   
12                    3841      1738.0710       1281.4290  1905.849582   
13                    3787         0.0000          0.0000  1322.132647   
14                    9005       994.6866        591.8004  1249.318351   
15                    6720      1876.9140       1618.9850  1214.378209   
16                    8545      1252.0050       1235.5770  1061.961113   
17                    3815      1876.9190       1047.6740  1308.664642   
18                    6440       875.3403       1035.7760  2729.685603   
19                    8540      1369.7750       1313.5470  2009.318579   
20                    3554      1365.6510       1012.7990   498.804543   
21                    4012         0.0000          0.0000  3247.303236   
22                    3508       834.5635        651.6735  3074.136764   
23                    4589       221.6403        131.7694  2099.389996   
24                    4173       782.5092        594.7244  3173.713704   
25                    2550         0.0000        801.4464   605.031447   
26                    4105      1178.6280        807.1788  1976.423416   
27                    4038       651.1269        526.2178  2034.171413   
28                    8813       875.0183        464.8092  3757.302405   
29                    3902         0.0000          0.0000  3007.571259   
...                    ...            ...             ...          ...   
7814                  9434       646.8029          0.0000   330.741734   
7815                  9678       639.8415          0.0000   418.323704   
7816                  8897      1316.9290        662.2171   607.470289   
7817                  9341      1312.9230        849.5093   694.357309   
7818                  9642       613.0061          0.0000   569.349788   
7819                  6647      1172.1610        674.7793  1139.989029   
7820                  4059      1198.5090          0.0000   692.955112   
7821                  9014      1350.5770        838.8643   809.819371   
7822                  9445      1296.2060        812.3987  1169.257483   
7823                  8930      1398.2330        879.5729   495.476819   
7824                  9457      1307.2390        835.6952   843.114626   
7825                  9480      1077.4830        847.9736   611.024075   
7826                  8971      2424.1120       1348.6120   609.965988   
7827                  8627      2391.5970       1441.0970   454.680978   
7828                  9382      2143.3760       1241.4700   609.038127   
7829                  9710       562.3441          0.0000   534.401136   
7830                  9684       584.5623          0.0000   556.290893   
7831                  4714       552.4348          0.0000   543.292103   
7832                  4779       266.3333          0.0000   397.645115   
7833                  9784       543.0637          0.0000   587.270156   
7834                  1659       522.7615          0.0000   495.260664   
7835                  9705      1297.6180        876.0724   674.773118   
7836      

In [77]:
x_train_new_3 = np.array(x_train_new_3_dataframe)
print(x_train_new_3.shape,y_train.shape)

(7844, 17) (7844, 1)


In [73]:
model = Sequential()
model.add(Dense(output_dim=10, activation='relu', input_dim=x_train_new_3.shape[1]))
model.add(Dense(output_dim=5, activation='relu'))
# model.add(Dense(output_dim=3, activation='relu'))
model.add(Dense(output_dim=y_train.shape[1], activation='relu'))
adam = Adam(lr=0.1)
model.compile(loss='mae', optimizer=adam)

c:\users\gigabyte\appdata\local\programs\python\python37\lib\site-packages\ipykernel_launcher.py:2: UserWarning: Update your `Dense` call to the Keras 2 API: `Dense(activation="relu", input_dim=12, units=10)`
  
c:\users\gigabyte\appdata\local\programs\python\python37\lib\site-packages\ipykernel_launcher.py:3: UserWarning: Update your `Dense` call to the Keras 2 API: `Dense(activation="relu", units=5)`
  This is separate from the ipykernel package so we can avoid doing imports until
c:\users\gigabyte\appdata\local\programs\python\python37\lib\site-packages\ipykernel_launcher.py:5: UserWarning: Update your `Dense` call to the Keras 2 API: `Dense(activation="relu", units=1)`
  """


In [74]:
model.fit(x_train_new_3,y_train,batch_size = 512, epochs= 20000 , verbose = 1,shuffle = True)

Epoch 1/20000
7844/7844 [==============================] - 0s 42us/step - loss: 70903.1785
Epoch 2/20000
7844/7844 [==============================] - 0s 2us/step - loss: 29274.7341
Epoch 3/20000
7844/7844 [==============================] - 0s 2us/step - loss: 25244.1591
Epoch 4/20000
7844/7844 [==============================] - 0s 2us/step - loss: 24172.6655
Epoch 5/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23890.1313
Epoch 6/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23689.5538
Epoch 7/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23693.9856
Epoch 8/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23797.0824
Epoch 9/20000
7844/7844 [==============================] - 0s 2us/step - loss: 24021.9900
Epoch 10/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23747.4951
Epoch 11/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23570.2047
Epoch 1

7844/7844 [==============================] - 0s 2us/step - loss: 23372.2538
Epoch 92/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23406.9892
Epoch 93/20000
7844/7844 [==============================] - 0s 3us/step - loss: 23935.2223
Epoch 94/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23654.8791
Epoch 95/20000
7844/7844 [==============================] - 0s 3us/step - loss: 23570.7831
Epoch 96/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23568.8197
Epoch 97/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23470.2989
Epoch 98/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23448.5335
Epoch 99/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23462.6596
Epoch 100/20000
7844/7844 [==============================] - 0s 3us/step - loss: 23353.1901
Epoch 101/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23718.3903
Epoch 102/20

7844/7844 [==============================] - 0s 2us/step - loss: 23279.5993
Epoch 181/20000
7844/7844 [==============================] - 0s 3us/step - loss: 23568.5980
Epoch 182/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23364.6603
Epoch 183/20000
7844/7844 [==============================] - 0s 3us/step - loss: 23397.2454
Epoch 184/20000
7844/7844 [==============================] - 0s 3us/step - loss: 23407.9852
Epoch 185/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23534.5267
Epoch 186/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23355.4494
Epoch 187/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23679.1200
Epoch 188/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23380.0876
Epoch 189/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23416.4057
Epoch 190/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23532.1848
Epoc

7844/7844 [==============================] - 0s 3us/step - loss: 23373.8128
Epoch 270/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23386.0149
Epoch 271/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23294.9791
Epoch 272/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23667.4954
Epoch 273/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23541.9642
Epoch 274/20000
7844/7844 [==============================] - 0s 2us/step - loss: 24092.6766
Epoch 275/20000
7844/7844 [==============================] - 0s 2us/step - loss: 24179.0211
Epoch 276/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23654.5019
Epoch 277/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23340.7991
Epoch 278/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23430.0463
Epoch 279/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23365.5370
Epoc

7844/7844 [==============================] - 0s 3us/step - loss: 23519.8144
Epoch 359/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23631.2155
Epoch 360/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23315.5232
Epoch 361/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23340.1763
Epoch 362/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23440.4270
Epoch 363/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23253.0058
Epoch 364/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23498.1481
Epoch 365/20000
7844/7844 [==============================] - 0s 3us/step - loss: 23352.7732
Epoch 366/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23480.9126
Epoch 367/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23341.3214
Epoch 368/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23301.6493
Epoc

...

7844/7844 [==============================] - 0s 2us/step - loss: 23320.8192
Epoch 14741/20000
7844/7844 [==============================] - 0s 3us/step - loss: 23517.1952
Epoch 14742/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23451.1757
Epoch 14743/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23294.4359
Epoch 14744/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23482.8940
Epoch 14745/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23273.8091
Epoch 14746/20000
7844/7844 [==============================] - 0s 3us/step - loss: 23430.2049
Epoch 14747/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23329.6502
Epoch 14748/20000
7844/7844 [==============================] - 0s 3us/step - loss: 23820.5499
Epoch 14749/20000
7844/7844 [==============================] - 0s 3us/step - loss: 23340.4010
Epoch 14750/20000
7844/7844 [==============================] - 0s 2us/step - l

7844/7844 [==============================] - 0s 3us/step - loss: 23680.6070
Epoch 14828/20000
7844/7844 [==============================] - 0s 3us/step - loss: 23712.2745
Epoch 14829/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23732.8419
Epoch 14830/20000
7844/7844 [==============================] - 0s 3us/step - loss: 23683.4282
Epoch 14831/20000
7844/7844 [==============================] - 0s 3us/step - loss: 23809.8923
Epoch 14832/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23729.1245
Epoch 14833/20000
7844/7844 [==============================] - 0s 3us/step - loss: 23621.4230
Epoch 14834/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23724.3679
Epoch 14835/20000
7844/7844 [==============================] - 0s 3us/step - loss: 24058.4836
Epoch 14836/20000
7844/7844 [==============================] - 0s 2us/step - loss: 24760.3488
Epoch 14837/20000
7844/7844 [==============================] - 0s 3us/step - l

7844/7844 [==============================] - 0s 2us/step - loss: 23274.8873
Epoch 14915/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23301.2860
Epoch 14916/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23343.8775
Epoch 14917/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23324.4919
Epoch 14918/20000
7844/7844 [==============================] - 0s 3us/step - loss: 23443.9700
Epoch 14919/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23356.3441
Epoch 14920/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23393.3259
Epoch 14921/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23654.9299
Epoch 14922/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23819.7900
Epoch 14923/20000
7844/7844 [==============================] - 0s 3us/step - loss: 23236.8230
Epoch 14924/20000
7844/7844 [==============================] - 0s 2us/step - l

7844/7844 [==============================] - 0s 3us/step - loss: 23391.8537
Epoch 15002/20000
7844/7844 [==============================] - 0s 3us/step - loss: 23319.6903
Epoch 15003/20000
7844/7844 [==============================] - 0s 3us/step - loss: 23395.8638
Epoch 15004/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23465.8063
Epoch 15005/20000
7844/7844 [==============================] - 0s 3us/step - loss: 23290.6353
Epoch 15006/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23241.8194
Epoch 15007/20000
7844/7844 [==============================] - 0s 3us/step - loss: 23271.5238
Epoch 15008/20000
7844/7844 [==============================] - 0s 3us/step - loss: 23311.2371
Epoch 15009/20000
7844/7844 [==============================] - 0s 3us/step - loss: 23321.3430
Epoch 15010/20000
7844/7844 [==============================] - 0s 2us/step - loss: 24046.1674
Epoch 15011/20000
7844/7844 [==============================] - 0s 3us/step - l

KeyboardInterrupt: 

In [93]:
pca = PCA(n_components=2)
principalComponents = pca.fit_transform(x_train_new_3)
# principalDf = pd.DataFrame(data = principalComponents
#              , columns = ['principal component 1', 'principal component 2'])
principalComponents.shape

(7844, 2)

In [89]:
model = Sequential()
model.add(Dense(output_dim=10, activation='relu', input_dim=principalComponents.shape[1]))
model.add(Dense(output_dim=5, activation='relu'))
# model.add(Dense(output_dim=3, activation='relu'))
model.add(Dense(output_dim=y_train.shape[1], activation='relu'))
adam = Adam(lr=0.1)
model.compile(loss='mae', optimizer=adam)

c:\users\gigabyte\appdata\local\programs\python\python37\lib\site-packages\ipykernel_launcher.py:2: UserWarning: Update your `Dense` call to the Keras 2 API: `Dense(activation="relu", input_dim=8, units=10)`
  
c:\users\gigabyte\appdata\local\programs\python\python37\lib\site-packages\ipykernel_launcher.py:3: UserWarning: Update your `Dense` call to the Keras 2 API: `Dense(activation="relu", units=5)`
  This is separate from the ipykernel package so we can avoid doing imports until
c:\users\gigabyte\appdata\local\programs\python\python37\lib\site-packages\ipykernel_launcher.py:5: UserWarning: Update your `Dense` call to the Keras 2 API: `Dense(activation="relu", units=1)`
  """


In [90]:
model.fit(principalComponents,y_train,batch_size = 512, epochs= 20000 , verbose = 1,shuffle = True)

Epoch 1/20000
7844/7844 [==============================] - 0s 51us/step - loss: 89457.0484
Epoch 2/20000
7844/7844 [==============================] - 0s 2us/step - loss: 48881.6150
Epoch 3/20000
7844/7844 [==============================] - 0s 2us/step - loss: 40859.4565
Epoch 4/20000
7844/7844 [==============================] - 0s 2us/step - loss: 37186.1792
Epoch 5/20000
7844/7844 [==============================] - 0s 2us/step - loss: 36205.2363
Epoch 6/20000
7844/7844 [==============================] - 0s 2us/step - loss: 35789.0730
Epoch 7/20000
7844/7844 [==============================] - 0s 2us/step - loss: 35148.6428
Epoch 8/20000
7844/7844 [==============================] - 0s 1us/step - loss: 34891.0564
Epoch 9/20000
7844/7844 [==============================] - 0s 2us/step - loss: 34292.6134
Epoch 10/20000
7844/7844 [==============================] - 0s 2us/step - loss: 34337.6099
Epoch 11/20000
7844/7844 [==============================] - 0s 2us/step - loss: 34045.0465
Epoch 1

7844/7844 [==============================] - 0s 3us/step - loss: 31350.1341
Epoch 92/20000
7844/7844 [==============================] - 0s 2us/step - loss: 31222.8646
Epoch 93/20000
7844/7844 [==============================] - 0s 2us/step - loss: 30901.1033
Epoch 94/20000
7844/7844 [==============================] - 0s 3us/step - loss: 30972.9463
Epoch 95/20000
7844/7844 [==============================] - 0s 2us/step - loss: 30676.2100
Epoch 96/20000
7844/7844 [==============================] - 0s 2us/step - loss: 31029.1141
Epoch 97/20000
7844/7844 [==============================] - 0s 2us/step - loss: 31034.6150
Epoch 98/20000
7844/7844 [==============================] - 0s 3us/step - loss: 30631.0140
Epoch 99/20000
7844/7844 [==============================] - 0s 3us/step - loss: 30960.8190
Epoch 100/20000
7844/7844 [==============================] - 0s 2us/step - loss: 30664.8906
Epoch 101/20000
7844/7844 [==============================] - 0s 2us/step - loss: 31274.8824
Epoch 102/20

7844/7844 [==============================] - 0s 2us/step - loss: 31318.6302
Epoch 181/20000
7844/7844 [==============================] - 0s 2us/step - loss: 30383.8906
Epoch 182/20000
7844/7844 [==============================] - 0s 2us/step - loss: 30257.8694
Epoch 183/20000
7844/7844 [==============================] - 0s 2us/step - loss: 30013.5984
Epoch 184/20000
7844/7844 [==============================] - 0s 2us/step - loss: 30133.4634
Epoch 185/20000
7844/7844 [==============================] - 0s 2us/step - loss: 30261.3771
Epoch 186/20000
7844/7844 [==============================] - 0s 2us/step - loss: 30225.4661
Epoch 187/20000
7844/7844 [==============================] - 0s 2us/step - loss: 30552.5203
Epoch 188/20000
7844/7844 [==============================] - 0s 2us/step - loss: 30421.0699
Epoch 189/20000
7844/7844 [==============================] - 0s 2us/step - loss: 31085.9199
Epoch 190/20000
7844/7844 [==============================] - 0s 2us/step - loss: 30297.1646
Epoc

7844/7844 [==============================] - 0s 2us/step - loss: 30122.0305
Epoch 270/20000
7844/7844 [==============================] - 0s 2us/step - loss: 30001.3968
Epoch 271/20000
7844/7844 [==============================] - 0s 2us/step - loss: 29912.0988
Epoch 272/20000
7844/7844 [==============================] - 0s 2us/step - loss: 29848.7812
Epoch 273/20000
7844/7844 [==============================] - 0s 2us/step - loss: 30132.7750
Epoch 274/20000
7844/7844 [==============================] - 0s 2us/step - loss: 29783.9979
Epoch 275/20000
7844/7844 [==============================] - 0s 2us/step - loss: 29946.7067
Epoch 276/20000
7844/7844 [==============================] - 0s 2us/step - loss: 30209.1738
Epoch 277/20000
7844/7844 [==============================] - 0s 2us/step - loss: 30254.6395
Epoch 278/20000
7844/7844 [==============================] - 0s 2us/step - loss: 30125.5529
Epoch 279/20000
7844/7844 [==============================] - 0s 2us/step - loss: 29772.1365
Epoc

7844/7844 [==============================] - 0s 2us/step - loss: 29666.5432
Epoch 359/20000
7844/7844 [==============================] - 0s 2us/step - loss: 29655.8503
Epoch 360/20000
7844/7844 [==============================] - 0s 2us/step - loss: 29624.3788
Epoch 361/20000
7844/7844 [==============================] - 0s 2us/step - loss: 30536.1859
Epoch 362/20000
7844/7844 [==============================] - 0s 2us/step - loss: 30459.9874
Epoch 363/20000
7844/7844 [==============================] - 0s 2us/step - loss: 30018.6287
Epoch 364/20000
7844/7844 [==============================] - 0s 3us/step - loss: 29877.6419
Epoch 365/20000
7844/7844 [==============================] - 0s 3us/step - loss: 29984.5640
Epoch 366/20000
7844/7844 [==============================] - 0s 2us/step - loss: 29595.8002
Epoch 367/20000
7844/7844 [==============================] - 0s 2us/step - loss: 29754.2777
Epoch 368/20000
7844/7844 [==============================] - 0s 2us/step - loss: 30064.0562
Epoc

...

7844/7844 [==============================] - 0s 2us/step - loss: 23516.6797
Epoch 5206/20000
7844/7844 [==============================] - 0s 3us/step - loss: 23194.6231
Epoch 5207/20000
7844/7844 [==============================] - 0s 3us/step - loss: 22832.3201
Epoch 5208/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22743.7908
Epoch 5209/20000
7844/7844 [==============================] - 0s 3us/step - loss: 24569.4419
Epoch 5210/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23929.2535
Epoch 5211/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23426.8893
Epoch 5212/20000
7844/7844 [==============================] - 0s 3us/step - loss: 22747.7035
Epoch 5213/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22996.2626
Epoch 5214/20000
7844/7844 [==============================] - 0s 3us/step - loss: 23393.7168
Epoch 5215/20000
7844/7844 [==============================] - 0s 2us/step - loss: 24527

7844/7844 [==============================] - 0s 2us/step - loss: 23413.6613
Epoch 5294/20000
7844/7844 [==============================] - 0s 2us/step - loss: 25803.1995
Epoch 5295/20000
7844/7844 [==============================] - 0s 3us/step - loss: 24434.2520
Epoch 5296/20000
7844/7844 [==============================] - 0s 2us/step - loss: 26405.7601
Epoch 5297/20000
7844/7844 [==============================] - 0s 3us/step - loss: 24512.0322
Epoch 5298/20000
7844/7844 [==============================] - 0s 3us/step - loss: 23536.7793
Epoch 5299/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23367.5633
Epoch 5300/20000
7844/7844 [==============================] - 0s 3us/step - loss: 24568.0876
Epoch 5301/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23647.5896
Epoch 5302/20000
7844/7844 [==============================] - 0s 2us/step - loss: 24634.6816
Epoch 5303/20000
7844/7844 [==============================] - 0s 2us/step - loss: 24325

7844/7844 [==============================] - 0s 2us/step - loss: 23976.4590
Epoch 5382/20000
7844/7844 [==============================] - 0s 3us/step - loss: 23644.2948
Epoch 5383/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23638.2089
Epoch 5384/20000
7844/7844 [==============================] - 0s 3us/step - loss: 23639.2158
Epoch 5385/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23646.1313
Epoch 5386/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23764.9031
Epoch 5387/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23518.1956
Epoch 5388/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23297.1536
Epoch 5389/20000
7844/7844 [==============================] - 0s 3us/step - loss: 23642.9161
Epoch 5390/20000
7844/7844 [==============================] - 0s 2us/step - loss: 24644.9043
Epoch 5391/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23592

7844/7844 [==============================] - 0s 2us/step - loss: 23712.9623
Epoch 5470/20000
7844/7844 [==============================] - 0s 3us/step - loss: 23443.2799
Epoch 5471/20000
7844/7844 [==============================] - 0s 3us/step - loss: 23587.0247
Epoch 5472/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23526.0456
Epoch 5473/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23155.2422
Epoch 5474/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23447.2139
Epoch 5475/20000
7844/7844 [==============================] - 0s 3us/step - loss: 23611.8107
Epoch 5476/20000
7844/7844 [==============================] - 0s 3us/step - loss: 23134.2094
Epoch 5477/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23063.0543
Epoch 5478/20000
7844/7844 [==============================] - 0s 3us/step - loss: 23108.7969
Epoch 5479/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23970

KeyboardInterrupt: 

In [94]:
clf = svm.SVR()
clf.fit(principalComponents,y_train)

c:\users\gigabyte\appdata\local\programs\python\python37\lib\site-packages\sklearn\utils\validation.py:761: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
c:\users\gigabyte\appdata\local\programs\python\python37\lib\site-packages\sklearn\svm\base.py:196: FutureWarning: The default value of gamma will change from 'auto' to 'scale' in version 0.22 to account better for unscaled features. Set gamma explicitly to 'auto' or 'scale' to avoid this warning.
  "avoid this warning.", FutureWarning)


SVR(C=1.0, cache_size=200, coef0=0.0, degree=3, epsilon=0.1,
  gamma='auto_deprecated', kernel='rbf', max_iter=-1, shrinking=True,
  tol=0.001, verbose=False)

In [95]:
clf.score(principalComponents,y_train)

-0.03420948680657143

In [108]:
Month1Production = production_data_train[production_data_train["Index"]==1]
m1prod = Month1Production[["API","Liquid"]]
m1prod.rename(columns={'Liquid':'Liquid1'}, inplace=True)
Month2Production = production_data_train[production_data_train["Index"]==2]
m2prod = Month2Production[["API","Liquid"]]
m2prod.rename(columns={'Liquid':'Liquid2'}, inplace=True)
Month3Production = production_data_train[production_data_train["Index"]==3]
m3prod = Month3Production[["API","Liquid"]]
m3prod.rename(columns={'Liquid':'Liquid3'}, inplace=True)
m3prod

API  Liquid3
0       33053063590000    10421
55      33053045990000     7231
121     33053051270000     4807
170     33053042370000     2424
218     33053058340000      200
282     33053064340000     6719
338     33053047160000     6808
382     05005071800000     4926
448     05005071920000     5703
497     05123384940000     4396
542     05123380310000     9468
603     05123376870000     3997
675     33053052840000     6206
727     33053053850000    11965
788     33053049310000    16359
840     33053057580000     9437
891     33053058050000    16011
936     33053056030100    15635
993     33053059630000    16472
1040    33053063980000     6580
1088    33053066090000     7978
1138    05123392540000     7642
1183    05123379370100     6846
1229    33053062710000     8375
1272    33053062060000     4063
1315    33053063570000    14300
1360    33053065360000    20301
1413    33053052560000    16008
1473    33053051370000    17750
1535    33053048250100     2569
...                ...      ...
392744  42329400420100     7393
392793  42461398000000     1013
392816  42329395990000     5189
392885  42301322000000    10930
392939  42389342360000     3741
392962  42227382510000    14398
393025  42389345740000     7968
393075  42389341840000    10802
393122  42389348230000    20278
393135  42383391630100     6618
393203  05123377590300     8942
393285  42389339130000    19038
393312  42329391530000    10121
393350  42135428650000    12978
393422  42389345680000     2679
393462  42389348680000    23121
393510  42389348690000    14984
393542  42389348390000    31051
393594  42389348360000    15024
393634  42389348350000    10019
393675  42495317050100     4375
393716  42371335000200     2121
393741  42105421820000     3521
393777  42105421850000     3485
393824  42105422020000     2035
393872  42105421830000     3868
393901  42105422370000     2562
393958  42105422030000     1834
393982  42461397710000     4217
394050  42301324920100     8387

[7832 rows x 2 columns]

In [119]:
month1added = pd.merge(temp4,m1prod,how = 'left',on='API')
month2added = pd.merge(month1added,m2prod,how = 'left',on='API')
month3added = pd.merge(month2added,m3prod,how = 'left',on='API')
month3added.fillna(0,inplace = True)
month3added

API  Liquid  LATERAL_LENGTH_BLEND  PROP_PER_FOOT  \
0     05001097720000   65412                  4358       760.4881   
1     05001097780100   84043                  4208       611.6503   
2     05001097800000   13471                  3983         0.0000   
3     05001097820000   12992                  4221       801.2611   
4     05001097830000   15195                  4027         0.0000   
5     05001098050100  176206                  8190      1408.8110   
6     05001098450000  180189                  4315         0.0000   
7     05005071800000  126323                  4053      3401.1990   
8     05005071890100   66150                  3745      1742.2890   
9     05005071920000  186252                  3866      1835.5640   
10    05005072090000  142882                  4079      1568.7120   
11    05005072120000   62652                  3262      1914.9830   
12    05005072140100   63836                  3841      1738.0710   
13    05005072150100   99022                  3787         0.0000   
14    05005072170100  234552                  9005       994.6866   
15    05005072190100  264294                  6720      1876.9140   
16    05005072210000  250013                  8545      1252.0050   
17    05005072220000  102986                  3815      1876.9190   
18    05005072250100  200616                  6440       875.3403   
19    05005072260000  217756                  8540      1369.7750   
20    05123315730000   20563                  3554      1365.6510   
21    05123331840000   17377                  4012         0.0000   
22    05123334240100   20788                  3508       834.5635   
23    05123349460000   91506                  4589       221.6403   
24    05123349600000   76262                  4173       782.5092   
25    05123349910100    7703                  2550         0.0000   
26    05123350610000   70095                  4105      1178.6280   
27    05123350770000   91265                  4038       651.1269   
28    05123352460000   28831                  8813       875.0183   
29    05123352590000   51454                  3902         0.0000   
...              ...     ...                   ...            ...   
7814  49021211170000  180118                  9434       646.8029   
7815  49021211180000  133436                  9678       639.8415   
7816  49021211280000  142229                  8897      1316.9290   
7817  49021211310000  201533                  9341      1312.9230   
7818  49021211320000   87110                  9642       613.0061   
7819  49021211460000   73927                  6647      1172.1610   
7820  49021211760000   31937                  4059      1198.5090   
7821  49021211780000  207008                  9014      1350.5770   
7822  49021211800000  236270                  9445      1296.2060   
7823  49021211820000  191163                  8930      1398.2330   
7824  49021212030000  146182                  9457      1307.2390   
7825  49021212280000  164647                  9480      1077.4830   
7826  49021212460000  222063                  8971      2424.1120   
7827  49021212470000  187938                  8627      2391.5970   
7828  49021212490000  236922                  9382      2143.3760   
7829  49021213620000   95972                  9710       562.3441   
7830  49021213990000   90304                  9684       584.5623   
7831  49021214000000   31496                  4714       552.4348   
7832  49021214010000   41765                  4779       266.3333   
7833  49021215910000   88956                  9784       543.0637   
7834  49021217890000   63698                  1659       522.7615   
7835  49021219480000  134031                  9705      1297.6180   
7836  49021221450000  161373                  9670       437.8219   
7837  49021222690000  106619                  9822       572.4443   
7838  49021222710000   71089                  9527       622.4385   
7839  49021222940000  227454                 10138      2534.0880   
7840  490212229

In [120]:
month3added.drop(['API','Liquid'],axis = 1 , inplace = True)
x_train_new_3 = np.array(month3added)
print(x_train_new_3.shape,y_train.shape)
x_train_new_3

(7844, 19) (7844, 1)


array([[ 4358.    ,   760.4881,   934.0413, ..., 11483.    ,  7054.    ,
         5049.    ],
       [ 4208.    ,   611.6503,   546.6923, ..., 13171.    ,  7623.    ,
         2247.    ],
       [ 3983.    ,     0.    ,     0.    , ...,  1359.    ,  1112.    ,
         1195.    ],
       ...,
       [ 8161.    ,  2202.056 ,  1387.139 , ..., 26863.    , 19486.    ,
        18469.    ],
       [ 4208.    ,   584.2202,   217.9879, ...,  3060.    ,  2294.    ,
         1460.    ],
       [ 4249.    ,   538.438 ,     0.    , ...,  4088.    ,  2897.    ,
         1854.    ]])

In [123]:
model = Sequential()
model.add(Dense(output_dim=10, activation='relu', input_dim=x_train_new_3.shape[1]))
model.add(Dense(output_dim=5, activation='relu'))
# model.add(Dense(output_dim=3, activation='relu'))
model.add(Dense(output_dim=y_train.shape[1], activation='relu'))
adam = Adam(lr=0.05)
model.compile(loss='mae', optimizer=adam)

c:\users\gigabyte\appdata\local\programs\python\python37\lib\site-packages\ipykernel_launcher.py:2: UserWarning: Update your `Dense` call to the Keras 2 API: `Dense(activation="relu", input_dim=19, units=10)`
  
c:\users\gigabyte\appdata\local\programs\python\python37\lib\site-packages\ipykernel_launcher.py:3: UserWarning: Update your `Dense` call to the Keras 2 API: `Dense(activation="relu", units=5)`
  This is separate from the ipykernel package so we can avoid doing imports until
c:\users\gigabyte\appdata\local\programs\python\python37\lib\site-packages\ipykernel_launcher.py:5: UserWarning: Update your `Dense` call to the Keras 2 API: `Dense(activation="relu", units=1)`
  """


In [124]:
model.fit(x_train_new_3,y_train,batch_size = 512, epochs= 20000 , verbose = 1,shuffle = True)

Epoch 1/20000
7844/7844 [==============================] - 1s 75us/step - loss: 68575.4493
Epoch 2/20000
7844/7844 [==============================] - 0s 2us/step - loss: 26875.3633
Epoch 3/20000
7844/7844 [==============================] - 0s 3us/step - loss: 24493.9507
Epoch 4/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23866.5956
Epoch 5/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23481.4500
Epoch 6/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23337.9093
Epoch 7/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23234.5176
Epoch 8/20000
7844/7844 [==============================] - 0s 2us/step - loss: 23239.9573
Epoch 9/20000
7844/7844 [==============================] - 0s 3us/step - loss: 23040.1462
Epoch 10/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22902.7007
Epoch 11/20000
7844/7844 [==============================] - 0s 3us/step - loss: 22875.5777
Epoch 1

7844/7844 [==============================] - 0s 3us/step - loss: 21574.1542
Epoch 92/20000
7844/7844 [==============================] - 0s 2us/step - loss: 21537.8789
Epoch 93/20000
7844/7844 [==============================] - 0s 3us/step - loss: 21903.6316
Epoch 94/20000
7844/7844 [==============================] - 0s 2us/step - loss: 21478.9060
Epoch 95/20000
7844/7844 [==============================] - 0s 2us/step - loss: 21398.4912
Epoch 96/20000
7844/7844 [==============================] - 0s 3us/step - loss: 21321.7068
Epoch 97/20000
7844/7844 [==============================] - 0s 2us/step - loss: 21379.3888
Epoch 98/20000
7844/7844 [==============================] - 0s 3us/step - loss: 21392.4040
Epoch 99/20000
7844/7844 [==============================] - 0s 2us/step - loss: 21978.6459
Epoch 100/20000
7844/7844 [==============================] - 0s 2us/step - loss: 21882.9206
Epoch 101/20000
7844/7844 [==============================] - 0s 2us/step - loss: 21579.4300
Epoch 102/20

7844/7844 [==============================] - 0s 3us/step - loss: 21395.7038
Epoch 181/20000
7844/7844 [==============================] - 0s 2us/step - loss: 21255.3464
Epoch 182/20000
7844/7844 [==============================] - 0s 3us/step - loss: 21305.7633
Epoch 183/20000
7844/7844 [==============================] - 0s 2us/step - loss: 21853.4765
Epoch 184/20000
7844/7844 [==============================] - 0s 2us/step - loss: 22127.4503
Epoch 185/20000
7844/7844 [==============================] - ETA: 0s - loss: 23678.863 - 0s 2us/step - loss: 21575.7259
Epoch 186/20000
7844/7844 [==============================] - 0s 3us/step - loss: 22051.8507
Epoch 187/20000
7844/7844 [==============================] - 0s 3us/step - loss: 22460.7693
Epoch 188/20000
7844/7844 [==============================] - 0s 2us/step - loss: 21740.7328
Epoch 189/20000
7844/7844 [==============================] - 0s 3us/step - loss: 21287.0444
Epoch 190/20000
7844/7844 [==============================] - 0s 2us/

7844/7844 [==============================] - 0s 2us/step - loss: 21859.4883
Epoch 269/20000
7844/7844 [==============================] - 0s 3us/step - loss: 21486.8689
Epoch 270/20000
7844/7844 [==============================] - 0s 2us/step - loss: 21319.5093
Epoch 271/20000
7844/7844 [==============================] - 0s 2us/step - loss: 21278.9276
Epoch 272/20000
7844/7844 [==============================] - 0s 3us/step - loss: 21281.8680
Epoch 273/20000
7844/7844 [==============================] - 0s 2us/step - loss: 21266.9005
Epoch 274/20000
7844/7844 [==============================] - 0s 3us/step - loss: 21408.9138
Epoch 275/20000
7844/7844 [==============================] - 0s 3us/step - loss: 21524.0353
Epoch 276/20000
7844/7844 [==============================] - 0s 2us/step - loss: 21293.2733
Epoch 277/20000
7844/7844 [==============================] - 0s 2us/step - loss: 21751.4109
Epoch 278/20000
7844/7844 [==============================] - 0s 2us/step - loss: 21275.0281
Epoc

7844/7844 [==============================] - 0s 2us/step - loss: 21349.9532
Epoch 358/20000
7844/7844 [==============================] - 0s 3us/step - loss: 21375.4296
Epoch 359/20000
7844/7844 [==============================] - 0s 2us/step - loss: 21373.1247
Epoch 360/20000
7844/7844 [==============================] - 0s 3us/step - loss: 21430.5963
Epoch 361/20000
7844/7844 [==============================] - 0s 2us/step - loss: 21288.7073
Epoch 362/20000
7844/7844 [==============================] - 0s 2us/step - loss: 21267.8178
Epoch 363/20000
7844/7844 [==============================] - 0s 2us/step - loss: 21260.2749
Epoch 364/20000
7844/7844 [==============================] - 0s 2us/step - loss: 21437.2689
Epoch 365/20000
7844/7844 [==============================] - 0s 3us/step - loss: 21310.2651
Epoch 366/20000
7844/7844 [==============================] - 0s 2us/step - loss: 21190.7037
Epoch 367/20000
7844/7844 [==============================] - 0s 3us/step - loss: 21200.0189
Epoc

...

7844/7844 [==============================] - 0s 3us/step - loss: 20339.6227
Epoch 10914/20000
7844/7844 [==============================] - 0s 3us/step - loss: 20395.4035
Epoch 10915/20000
7844/7844 [==============================] - 0s 3us/step - loss: 20233.1682
Epoch 10916/20000
7844/7844 [==============================] - 0s 3us/step - loss: 20359.4852
Epoch 10917/20000
7844/7844 [==============================] - 0s 3us/step - loss: 20355.6793
Epoch 10918/20000
7844/7844 [==============================] - 0s 3us/step - loss: 20292.9393
Epoch 10919/20000
7844/7844 [==============================] - 0s 3us/step - loss: 20316.0186
Epoch 10920/20000
7844/7844 [==============================] - 0s 3us/step - loss: 20635.9943
Epoch 10921/20000
7844/7844 [==============================] - 0s 3us/step - loss: 20562.3197
Epoch 10922/20000
7844/7844 [==============================] - 0s 3us/step - loss: 20366.2693
Epoch 10923/20000
7844/7844 [==============================] - 0s 3us/step - l

7844/7844 [==============================] - 0s 3us/step - loss: 20454.7128
Epoch 11001/20000
7844/7844 [==============================] - 0s 3us/step - loss: 20320.9720
Epoch 11002/20000
7844/7844 [==============================] - 0s 3us/step - loss: 20264.6787
Epoch 11003/20000
7844/7844 [==============================] - 0s 3us/step - loss: 20498.5534
Epoch 11004/20000
7844/7844 [==============================] - 0s 3us/step - loss: 20543.0518
Epoch 11005/20000
7844/7844 [==============================] - 0s 3us/step - loss: 20562.2319
Epoch 11006/20000
7844/7844 [==============================] - 0s 3us/step - loss: 20556.8983
Epoch 11007/20000
7844/7844 [==============================] - 0s 2us/step - loss: 20489.0129
Epoch 11008/20000
7844/7844 [==============================] - 0s 3us/step - loss: 20428.9327
Epoch 11009/20000
7844/7844 [==============================] - 0s 3us/step - loss: 20357.8809
Epoch 11010/20000
7844/7844 [==============================] - 0s 3us/step - l

7844/7844 [==============================] - 0s 3us/step - loss: 20299.3521
Epoch 11088/20000
7844/7844 [==============================] - 0s 3us/step - loss: 20447.0769
Epoch 11089/20000
7844/7844 [==============================] - 0s 3us/step - loss: 20355.5132
Epoch 11090/20000
7844/7844 [==============================] - 0s 3us/step - loss: 20314.8360
Epoch 11091/20000
7844/7844 [==============================] - 0s 3us/step - loss: 20332.4250
Epoch 11092/20000
7844/7844 [==============================] - 0s 3us/step - loss: 20450.6277
Epoch 11093/20000
7844/7844 [==============================] - 0s 3us/step - loss: 20408.1480
Epoch 11094/20000
7844/7844 [==============================] - 0s 3us/step - loss: 20278.3928
Epoch 11095/20000
7844/7844 [==============================] - 0s 3us/step - loss: 20285.1714
Epoch 11096/20000
7844/7844 [==============================] - 0s 3us/step - loss: 20251.9559
Epoch 11097/20000
7844/7844 [==============================] - 0s 3us/step - l

7844/7844 [==============================] - 0s 3us/step - loss: 20438.8481
Epoch 11175/20000
7844/7844 [==============================] - 0s 3us/step - loss: 20302.5801
Epoch 11176/20000
7844/7844 [==============================] - 0s 3us/step - loss: 20242.6806
Epoch 11177/20000
7844/7844 [==============================] - 0s 3us/step - loss: 20250.4700
Epoch 11178/20000
7844/7844 [==============================] - 0s 3us/step - loss: 20500.4156
Epoch 11179/20000
7844/7844 [==============================] - 0s 3us/step - loss: 20610.2061
Epoch 11180/20000
7844/7844 [==============================] - 0s 3us/step - loss: 20281.2114
Epoch 11181/20000
7844/7844 [==============================] - 0s 3us/step - loss: 20307.4764
Epoch 11182/20000
7844/7844 [==============================] - 0s 3us/step - loss: 20390.7601
Epoch 11183/20000
7844/7844 [==============================] - 0s 3us/step - loss: 20284.1970
Epoch 11184/20000
7844/7844 [==============================] - 0s 3us/step - l

KeyboardInterrupt: 

In [136]:
pca = PCA(n_components=2)
principalComponents = pca.fit_transform(x_train_new_3)
principalComponents.shape

(7844, 2)

In [143]:
model = Sequential()
model.add(Dense(output_dim=2, activation='relu', input_dim=principalComponents.shape[1]))
model.add(Dense(output_dim=2, activation='relu'))
# model.add(Dense(output_dim=3, activation='relu'))
model.add(Dense(output_dim=y_train.shape[1], activation='relu'))
adam = Adam(lr=0.1)
model.compile(loss='mae', optimizer=adam)

c:\users\gigabyte\appdata\local\programs\python\python37\lib\site-packages\ipykernel_launcher.py:2: UserWarning: Update your `Dense` call to the Keras 2 API: `Dense(activation="relu", input_dim=2, units=2)`
  
c:\users\gigabyte\appdata\local\programs\python\python37\lib\site-packages\ipykernel_launcher.py:3: UserWarning: Update your `Dense` call to the Keras 2 API: `Dense(activation="relu", units=2)`
  This is separate from the ipykernel package so we can avoid doing imports until
c:\users\gigabyte\appdata\local\programs\python\python37\lib\site-packages\ipykernel_launcher.py:5: UserWarning: Update your `Dense` call to the Keras 2 API: `Dense(activation="relu", units=1)`
  """


In [144]:
model.fit(principalComponents,y_train,batch_size = 512, epochs= 20000 , verbose = 1,shuffle = True)

Epoch 1/20000
7844/7844 [==============================] - 1s 85us/step - loss: 111298.0332
Epoch 2/20000
7844/7844 [==============================] - 0s 3us/step - loss: 57556.6530
Epoch 3/20000
7844/7844 [==============================] - 0s 2us/step - loss: 47586.9440
Epoch 4/20000
7844/7844 [==============================] - 0s 2us/step - loss: 46609.6484
Epoch 5/20000
7844/7844 [==============================] - 0s 3us/step - loss: 46155.2246
Epoch 6/20000
7844/7844 [==============================] - 0s 2us/step - loss: 46037.6143
Epoch 7/20000
7844/7844 [==============================] - 0s 2us/step - loss: 45692.2729
Epoch 8/20000
7844/7844 [==============================] - 0s 2us/step - loss: 45268.6629
Epoch 9/20000
7844/7844 [==============================] - 0s 3us/step - loss: 45142.4200
Epoch 10/20000
7844/7844 [==============================] - 0s 2us/step - loss: 45254.3326
Epoch 11/20000
7844/7844 [==============================] - 0s 2us/step - loss: 45232.2435
Epoch 

7844/7844 [==============================] - 0s 2us/step - loss: 44950.8260
Epoch 92/20000
7844/7844 [==============================] - 0s 3us/step - loss: 44937.8122
Epoch 93/20000
7844/7844 [==============================] - 0s 2us/step - loss: 45071.8189
Epoch 94/20000
7844/7844 [==============================] - 0s 3us/step - loss: 44957.9490
Epoch 95/20000
7844/7844 [==============================] - 0s 2us/step - loss: 44923.5843
Epoch 96/20000
7844/7844 [==============================] - 0s 2us/step - loss: 44767.4115
Epoch 97/20000
7844/7844 [==============================] - 0s 2us/step - loss: 44712.0315
Epoch 98/20000
7844/7844 [==============================] - 0s 2us/step - loss: 44736.8331
Epoch 99/20000
7844/7844 [==============================] - 0s 3us/step - loss: 44758.4675
Epoch 100/20000
7844/7844 [==============================] - 0s 2us/step - loss: 44755.3454
Epoch 101/20000
7844/7844 [==============================] - 0s 2us/step - loss: 44885.0133
Epoch 102/20

7844/7844 [==============================] - 0s 2us/step - loss: 44230.3649
Epoch 181/20000
7844/7844 [==============================] - 0s 3us/step - loss: 44848.3998
Epoch 182/20000
7844/7844 [==============================] - 0s 2us/step - loss: 44067.9655
Epoch 183/20000
7844/7844 [==============================] - 0s 2us/step - loss: 43966.7815
Epoch 184/20000
7844/7844 [==============================] - 0s 3us/step - loss: 43996.8566
Epoch 185/20000
7844/7844 [==============================] - 0s 2us/step - loss: 43810.0407
Epoch 186/20000
7844/7844 [==============================] - 0s 3us/step - loss: 44183.5017
Epoch 187/20000
7844/7844 [==============================] - 0s 2us/step - loss: 44069.6094
Epoch 188/20000
7844/7844 [==============================] - 0s 2us/step - loss: 44244.7784
Epoch 189/20000
7844/7844 [==============================] - 0s 3us/step - loss: 44465.5372
Epoch 190/20000
7844/7844 [==============================] - 0s 2us/step - loss: 44278.2924
Epoc

7844/7844 [==============================] - 0s 2us/step - loss: 34313.9573
Epoch 270/20000
7844/7844 [==============================] - 0s 3us/step - loss: 37086.8373
Epoch 271/20000
7844/7844 [==============================] - 0s 3us/step - loss: 37603.5288
Epoch 272/20000
7844/7844 [==============================] - 0s 2us/step - loss: 33005.1161
Epoch 273/20000
7844/7844 [==============================] - 0s 2us/step - loss: 34145.5954
Epoch 274/20000
7844/7844 [==============================] - 0s 2us/step - loss: 34498.2836
Epoch 275/20000
7844/7844 [==============================] - 0s 3us/step - loss: 61006.3616
Epoch 276/20000
7844/7844 [==============================] - 0s 2us/step - loss: 41034.8486
Epoch 277/20000
7844/7844 [==============================] - 0s 3us/step - loss: 36401.6158
Epoch 278/20000
7844/7844 [==============================] - 0s 3us/step - loss: 35308.9948
Epoch 279/20000
7844/7844 [==============================] - 0s 2us/step - loss: 34980.7485
Epoc

7844/7844 [==============================] - 0s 2us/step - loss: 28417.5921
Epoch 359/20000
7844/7844 [==============================] - 0s 2us/step - loss: 27728.8115
Epoch 360/20000
7844/7844 [==============================] - 0s 3us/step - loss: 32572.5651
Epoch 361/20000
7844/7844 [==============================] - 0s 3us/step - loss: 30781.4621
Epoch 362/20000
7844/7844 [==============================] - 0s 2us/step - loss: 30761.2782
Epoch 363/20000
7844/7844 [==============================] - 0s 3us/step - loss: 32102.1401
Epoch 364/20000
7844/7844 [==============================] - 0s 2us/step - loss: 29114.0285
Epoch 365/20000
7844/7844 [==============================] - 0s 2us/step - loss: 27497.7869
Epoch 366/20000
7844/7844 [==============================] - 0s 2us/step - loss: 27756.3995
Epoch 367/20000
7844/7844 [==============================] - 0s 2us/step - loss: 28088.7730
Epoch 368/20000
7844/7844 [==============================] - 0s 2us/step - loss: 27658.5596
Epoc

...

7844/7844 [==============================] - 0s 3us/step - loss: 25662.6662
Epoch 3270/20000
7844/7844 [==============================] - 0s 2us/step - loss: 26270.5808
Epoch 3271/20000
7844/7844 [==============================] - 0s 2us/step - loss: 26128.2701
Epoch 3272/20000
7844/7844 [==============================] - 0s 3us/step - loss: 26082.9865
Epoch 3273/20000
7844/7844 [==============================] - 0s 3us/step - loss: 25445.2268
Epoch 3274/20000
7844/7844 [==============================] - 0s 3us/step - loss: 25174.6950
Epoch 3275/20000
7844/7844 [==============================] - 0s 3us/step - loss: 25485.2171
Epoch 3276/20000
7844/7844 [==============================] - 0s 2us/step - loss: 27702.1830
Epoch 3277/20000
7844/7844 [==============================] - 0s 3us/step - loss: 26279.1919
Epoch 3278/20000
7844/7844 [==============================] - 0s 2us/step - loss: 28276.0065
Epoch 3279/20000
7844/7844 [==============================] - 0s 3us/step - loss: 26920

7844/7844 [==============================] - 0s 2us/step - loss: 26054.3089
Epoch 3358/20000
7844/7844 [==============================] - 0s 3us/step - loss: 25478.6332
Epoch 3359/20000
7844/7844 [==============================] - 0s 2us/step - loss: 25157.9328
Epoch 3360/20000
7844/7844 [==============================] - 0s 3us/step - loss: 25859.1620
Epoch 3361/20000
7844/7844 [==============================] - 0s 3us/step - loss: 26302.0857
Epoch 3362/20000
7844/7844 [==============================] - 0s 3us/step - loss: 26472.4310
Epoch 3363/20000
7844/7844 [==============================] - 0s 2us/step - loss: 25788.9738
Epoch 3364/20000
7844/7844 [==============================] - 0s 3us/step - loss: 26502.8115
Epoch 3365/20000
7844/7844 [==============================] - 0s 3us/step - loss: 25410.9399
Epoch 3366/20000
7844/7844 [==============================] - 0s 2us/step - loss: 25345.0726
Epoch 3367/20000
7844/7844 [==============================] - 0s 3us/step - loss: 25639

7844/7844 [==============================] - 0s 3us/step - loss: 25523.2112
Epoch 3446/20000
7844/7844 [==============================] - 0s 3us/step - loss: 25256.7318
Epoch 3447/20000
7844/7844 [==============================] - 0s 2us/step - loss: 25173.6600
Epoch 3448/20000
7844/7844 [==============================] - 0s 3us/step - loss: 26073.3788
Epoch 3449/20000
7844/7844 [==============================] - 0s 2us/step - loss: 26414.2223
Epoch 3450/20000
7844/7844 [==============================] - 0s 2us/step - loss: 25950.4699
Epoch 3451/20000
7844/7844 [==============================] - 0s 3us/step - loss: 27359.4353
Epoch 3452/20000
7844/7844 [==============================] - 0s 3us/step - loss: 26393.1957
Epoch 3453/20000
7844/7844 [==============================] - 0s 2us/step - loss: 25772.3564
Epoch 3454/20000
7844/7844 [==============================] - 0s 3us/step - loss: 25734.2956
Epoch 3455/20000
7844/7844 [==============================] - 0s 2us/step - loss: 27836

7844/7844 [==============================] - 0s 3us/step - loss: 25437.2293
Epoch 3534/20000
7844/7844 [==============================] - 0s 2us/step - loss: 25487.8205
Epoch 3535/20000
7844/7844 [==============================] - 0s 2us/step - loss: 26473.7160
Epoch 3536/20000
7844/7844 [==============================] - 0s 2us/step - loss: 27039.5529
Epoch 3537/20000
7844/7844 [==============================] - 0s 2us/step - loss: 25527.7286
Epoch 3538/20000
7844/7844 [==============================] - 0s 3us/step - loss: 25377.6837
Epoch 3539/20000
7844/7844 [==============================] - 0s 3us/step - loss: 25288.9035
Epoch 3540/20000
7844/7844 [==============================] - 0s 3us/step - loss: 25740.5614
Epoch 3541/20000
7844/7844 [==============================] - 0s 3us/step - loss: 26145.5124
Epoch 3542/20000
7844/7844 [==============================] - 0s 3us/step - loss: 25632.5201
Epoch 3543/20000
7844/7844 [==============================] - 0s 3us/step - loss: 25204

KeyboardInterrupt: 